# Data Augmentation
1. add to image
2. add to annotations (train_all)
3. extract features again

### Use baseline as kernel

In [1]:
img_path = 'data/img'
ann_path = 'mmf/data/datasets/mami/defaults/annotations'

In [3]:
import os
import imageio
import imgaug as ia
import imgaug.augmenters as iaa
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import matplotlib
import random
from sklearn.utils import shuffle
home = 'home/taochen'

In [6]:
# false_prediction = pd.read_csv('false_prediction.csv')
# img_list = false_prediction['id']

truth_all = pd.read_json(ann_path+'/train1.jsonl', orient='records', lines=True)
# random_list = random.sample(range(0, 8999), 150)
# random_list = truth_all.iloc[random_list]['img'].str.split('/').str.get(1)
# img_list = pd.concat([img_list, img_list, random_list]).values
img_list = pd.read_csv('img_list.csv')['0']

In [7]:
def transform(image):
    rotate = iaa.Affine(rotate=(-10, 30))
    gaussian_noise = iaa.AdditiveGaussianNoise(5,15)
    blur = iaa.GaussianBlur(sigma=(0.5, 2.0))
    flip_hr = iaa.Fliplr(p=1.0)
    contrast = iaa.GammaContrast(gamma=2.0)
    scale_im = iaa.Affine(scale={"x": (1.5, 1.0), "y": (1.5, 1.0)})
    distort = iaa.PiecewiseAffine(scale=(0.01, 0.05))
    elastic = iaa.ElasticTransformation(alpha=(0, 5.0), sigma=0.25)
    saturation = iaa.WithHueAndSaturation(iaa.WithChannels(0, iaa.Add((0, 50))))
    
    aug_list = [rotate, gaussian_noise, blur, flip_hr, contrast, scale_im, distort, elastic, saturation]
    aug_type = random.randint(0, 8)
    image = aug_list[aug_type].augment_image(image)
    return image

In [8]:
def data_augmentation(truth_all, img_list, ann_path, img_path):
    for i in range(len(img_list)):
        img_name = img_list[i]
        image = imageio.imread(os.path.join(img_path, img_name))
        transformed_image = transform(image)
        new_index = 20001+i
        imageio.imwrite(img_path+'/'+str(new_index)+'.jpg', transformed_image)
        temp = truth_all.loc[truth_all['id'] == int(img_name[:-4])]
        temp[['id', 'img']] = [new_index, 'img/' + str(new_index) + '.jpg']
        truth_all = pd.concat([truth_all, temp], axis=0)
    truth_all = shuffle(truth_all)
    truth_all.to_json(ann_path + '/train11.jsonl', lines=True, orient='records')

In [9]:
img_list = img_list.to_list()
img_list.remove('.DS_Store')
img_list += img_list
len(img_list)

852

In [10]:
truth_all.shape

(9000, 8)

In [11]:
import warnings
warnings.filterwarnings("ignore")
data_augmentation(truth_all, img_list, ann_path, img_path)

In [19]:
new_train = pd.read_json(ann_path + '/train11.jsonl', lines=True, orient='records')
for col_name in ['misogynous', 'shaming', 'stereotype', 'objectification', 'violence']:
    col = new_train[['id', 'img', col_name, 'text']].rename(columns={col_name: 'label'})
    path = ann_path + '/train_' + col_name + '11.jsonl'
    col.to_json(path, lines=True, orient='records')

### Use mmf as kernel

# Feature Extraction

In [1]:
import os
home = '/home/taochen'
os.chdir(os.path.join(home, "vqa-maskrcnn-benchmark"))
!rm -rf build

In [2]:
!python setup.py build develop

running build
running build_py
creating build
creating build/lib.linux-x86_64-3.7
creating build/lib.linux-x86_64-3.7/maskrcnn_benchmark
copying maskrcnn_benchmark/__init__.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark
creating build/lib.linux-x86_64-3.7/maskrcnn_benchmark/config
copying maskrcnn_benchmark/config/__init__.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark/config
copying maskrcnn_benchmark/config/paths_catalog.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark/config
copying maskrcnn_benchmark/config/defaults.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark/config
creating build/lib.linux-x86_64-3.7/maskrcnn_benchmark/modeling
copying maskrcnn_benchmark/modeling/matcher.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark/modeling
copying maskrcnn_benchmark/modeling/poolers.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark/modeling
copying maskrcnn_benchmark/modeling/__init__.py -> build/lib.linux-x86_64-3.7/maskrcnn_benchmark/modeling
copying maskrcnn_bench

building 'maskrcnn_benchmark._C' extension
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu
creating /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cuda
Emitting ninja build file /home/taochen/vqa-maskrcnn-benchmark/buil

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             ^
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/ATen/core/TensorBody.h:354:1: note: declared here
   T * data() const {
 ^ ~~


[4/6] c++ -MMD -MF /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/ROIAlign_cpu.o.d -pthread -B /home/yewlee/miniconda3/envs/mmf/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -DWITH_CUDA -I/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/TH -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/THC -I/usr/local/cuda-10.2/include -I/home/yewlee/miniconda3/envs/mmf/include/python3.7m -c -c /home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/ROIAlign_cpu.cpp -o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchma

[5/6] c++ -MMD -MF /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/nms_cpu.o.d -pthread -B /home/yewlee/miniconda3/envs/mmf/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -DWITH_CUDA -I/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/TH -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/THC -I/usr/local/cuda-10.2/include -I/home/yewlee/miniconda3/envs/mmf/include/python3.7m -c -c /home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/nms_cpu.cpp -o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcn

...

[4/6] c++ -MMD -MF /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/ROIAlign_cpu.o.d -pthread -B /home/yewlee/miniconda3/envs/mmf/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -DWITH_CUDA -I/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/TH -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/THC -I/usr/local/cuda-10.2/include -I/home/yewlee/miniconda3/envs/mmf/include/python3.7m -c -c /home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/ROIAlign_cpu.cpp -o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchma

[5/6] c++ -MMD -MF /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/nms_cpu.o.d -pthread -B /home/yewlee/miniconda3/envs/mmf/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -DWITH_CUDA -I/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/TH -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/THC -I/usr/local/cuda-10.2/include -I/home/yewlee/miniconda3/envs/mmf/include/python3.7m -c -c /home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/nms_cpu.cpp -o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcn

                 from /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include/torch/data/dataloader/base.h:3,
                 from /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include/torch/data/dataloader/stateful.h:3,
                 from /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include/torch/data/dataloader.h:3,
                 from /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include/torch/data.h:3,
                 from /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include/torch/all.h:4,
                 from /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/extension.h:4,
                 from /home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/vision.h:3,
                 from /home/taochen/vqa-maskrcnn-benchmar

[6/6] c++ -MMD -MF /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/vision.o.d -pthread -B /home/yewlee/miniconda3/envs/mmf/compiler_compat -Wl,--sysroot=/ -Wsign-compare -DNDEBUG -g -fwrapv -O3 -Wall -Wstrict-prototypes -fPIC -DWITH_CUDA -I/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/torch/csrc/api/include -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/TH -I/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/include/THC -I/usr/local/cuda-10.2/include -I/home/yewlee/miniconda3/envs/mmf/include/python3.7m -c -c /home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/vision.cpp -o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmar

g++ -pthread -shared -B /home/yewlee/miniconda3/envs/mmf/compiler_compat -L/home/yewlee/miniconda3/envs/mmf/lib -Wl,-rpath=/home/yewlee/miniconda3/envs/mmf/lib -Wl,--no-as-needed -Wl,--sysroot=/ /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/vision.o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/nms_cpu.o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cpu/ROIAlign_cpu.o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cuda/nms.o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/csrc/cuda/ROIAlign_cuda.o /home/taochen/vqa-maskrcnn-benchmark/build/temp.linux-x86_64-3.7/home/taochen/vqa-maskrcnn-benchmark/maskr

In [3]:
# Extract features
os.chdir(os.path.join(home, "mmf/tools/scripts/features/"))
out_folder = os.path.join(home, "new_features/")

!python extract_features_vmb.py --config_file "https://dl.fbaipublicfiles.com/pythia/detectron_model/detectron_model_x152.yaml" \
                                --model_name "X-152" \
                                --output_folder $out_folder \
                                --image_dir "/home/taochen/data/img" \
                                --num_features 100

2022-01-27 12:14:36.862636: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 12:14:36.862662: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
model and config file exists in directory: /home/taochen/mmf/tools/scripts/features
/home/taochen/vqa-maskrcnn-benchmark/maskrcnn_benchmark/structures/boxlist_ops.py:45: UserWarning: This overload of nonzero is deprecated:
	nonzero()
Consider using one of the following signatures instead:
	nonzero(*, bool as_tuple) (Triggered internally at  /pytorch/torch/csrc/utils/python_arg_parser.cpp:766.)
  keep = ((ws >= min_size) & (hs >= min_size)).nonzero().squeeze(1)
Processed 200/11000
Processed 400/11000
Processed 600/11000
Processed 800/11000
Processed 1000/11000
Processed 1200/11000
Processed 1400/11000
Proc

# Train mmf models

## misogynous

In [1]:
import os
home = "/home/taochen"
os.chdir(home)
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_misogynous11.jsonl")

!mmf_run config="projects/visual_bert/configs/mami/from_coco.yaml" \
        model="visual_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        checkpoint.resume_zoo=visual_bert.pretrained.cc.full \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_misogynous.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=lr_testing/misogynous_individual \
        env.tensorboard_logdir=new_logs/fit/misogynous_individual_lr_testing

2022-01-27 22:09:16.051209: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 22:09:16.051233: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-27T22:09:21 | mmf.utils.configuration: Overriding option config to projects/visual_bert/configs/mami/from_coco.yaml
2022-01-27T22:09:21 | 

2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.dense.bias from model.bert.encoder.layer.1.attention.output.dense.bias
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.LayerNorm.weight from model.bert.encoder.layer.1.attention.output.LayerNorm.weight
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.LayerNorm.bias from model.bert.encoder.layer.1.attention.output.LayerNorm.bias
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.intermediate.dense.weight from model.bert.encoder.layer.1.intermediate.dense.weight
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.intermediate.dense.bias from model.bert.encoder.layer.1.intermediate.dense.bias
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.output.dense.weight from model.bert.encoder.layer.1.output.dense.weight
2022-0

2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.output.dense.bias from model.bert.encoder.layer.7.output.dense.bias
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.output.LayerNorm.weight from model.bert.encoder.layer.7.output.LayerNorm.weight
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.output.LayerNorm.bias from model.bert.encoder.layer.7.output.LayerNorm.bias
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.attention.self.query.weight from model.bert.encoder.layer.8.attention.self.query.weight
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.attention.self.query.bias from model.bert.encoder.layer.8.attention.self.query.bias
2022-01-27T22:09:32 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.attention.self.key.weight from model.bert.encoder.layer.8.attention.self.key.weight
2022-01-27T22:09:32 | mmf.utils.checkpoint: Co

2022-01-27T22:09:47 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T22:09:47 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T22:09:47 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T22:09:59 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.7414, train/mami/cross_entropy/avg: 0.7414, train/total_loss: 0.7414, train/total_loss/avg: 0.7414, max mem: 5481.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0.00001, ups: 1.92, time

2022-01-27T22:12:04 | mmf.trainers.callbacks.logistics: progress: 150/2000, train/mami/cross_entropy: 0.7323, train/mami/cross_entropy/avg: 0.7149, train/total_loss: 0.7323, train/total_loss/avg: 0.7149, max mem: 5484.0, experiment: run, epoch: 1, num_updates: 150, iterations: 150, max_updates: 2000, lr: 0.00002, ups: 1.85, time: 27s 178ms, time_since_start: 02m 32s 988ms, eta: 17m 45s 940ms
2022-01-27T22:12:04 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:12:11 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=Use

...

2022-01-27T22:39:28 | mmf.trainers.callbacks.logistics: progress: 1650/2000, train/mami/cross_entropy: 0.1579, train/mami/cross_entropy/avg: 0.3268, train/total_loss: 0.1579, train/total_loss/avg: 0.3268, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1650, iterations: 1650, max_updates: 2000, lr: 0.00001, ups: 2.08, time: 24s 558ms, time_since_start: 29m 56s 608ms, eta: 03m 02s 226ms
2022-01-27T22:39:28 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:39:35 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-27T22:41:03 | mmf.trainers.callbacks.logistics: progress: 1750/2000, train/mami/cross_entropy: 0.1262, train/mami/cross_entropy/avg: 0.3176, train/total_loss: 0.1262, train/total_loss/avg: 0.3176, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1750, iterations: 1750, max_updates: 2000, lr: 0., ups: 2.08, time: 24s 823ms, time_since_start: 31m 32s 404ms, eta: 02m 11s 565ms
2022-01-27T22:41:03 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:41:11 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-27T22:42:44 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.0583, train/mami/cross_entropy/avg: 0.3015, train/total_loss: 0.0583, train/total_loss/avg: 0.3015, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 1.79, time: 28s 584ms, time_since_start: 33m 12s 571ms, eta: 01m 30s 899ms
2022-01-27T22:42:44 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:42:51 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-27T22:44:29 | mmf.trainers.callbacks.logistics: progress: 1950/2000, train/mami/cross_entropy: 0.0468, train/mami/cross_entropy/avg: 0.2879, train/total_loss: 0.0468, train/total_loss/avg: 0.2879, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1950, iterations: 1950, max_updates: 2000, lr: 0., ups: 1.79, time: 28s 090ms, time_since_start: 34m 57s 497ms, eta: 29s 776ms
2022-01-27T22:44:29 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:44:36 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarni

100%|███████████████████████████████████████████| 63/63 [00:07<00:00,  8.71it/s]
2022-01-27T22:45:54 | mmf.trainers.callbacks.logistics: progress: 1600/2000, val/mami/cross_entropy: 0.5269, val/total_loss: 0.5269, val/mami/scoreA: 0.8438, val/mami/binary_f1: 0.8491, val/mami/roc_auc: 0.9148
2022-01-27T22:45:54 | mmf.trainers.callbacks.logistics: Finished run in 36m 23s 283ms


In [5]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_misogynous11.jsonl")

!mmf_run config="projects/others/concat_bert/mami/defaults.yaml" \
        model="concat_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_misogynous.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/concat_bert_misogynous \
        env.tensorboard_logdir=new_logs/fit/concat_bert_misogynous

2022-01-27 16:11:32.259395: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 16:11:32.259419: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2022-01-27T16:11:38 | mmf.utils.configuration: Overriding option config to projects/others/concat_bert/mami/defaults.yaml
2022-01-27T16:11:38 | mmf.utils.configuration: Overriding option model to concat_bert
2022-01-27T16:11:38 | mmf.utils.configuration: Overriding option datasets to mami
2022-01-27T16:11:38 | mmf.utils.configuration: Overriding option run_type to train_val
2022-01-27T16:11:38 | mmf.utils.configuration: Overriding option checkpoint.max_to_keep to 1
2022-01-27T16:11:38 | mmf.utils.configuration: Overriding option training.tensorboard to True
2022-01-27T16:11:38 | mmf.utils.configuration: O

2022-01-27T16:11:56 | mmf.utils.general: Total Parameters: 170384706. Trained Parameters: 170384706
2022-01-27T16:11:56 | mmf.trainers.core.training_loop: Starting training...
2022-01-27T16:12:15 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T16:12:15 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:12:15 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T16:12:30 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.7239, train/mami/cross_entropy/avg: 0.7239, trai

2022-01-27T16:17:56 | mmf.trainers.callbacks.logistics: progress: 200/2000, val/mami/cross_entropy: 0.6229, val/total_loss: 0.6229, val/mami/scoreA: 0.6423, val/mami/binary_f1: 0.7124, val/mami/roc_auc: 0.7290, num_updates: 200, epoch: 1, iterations: 200, max_updates: 2000, val_time: 44s 559ms, best_update: 200, best_iteration: 200, best_val/mami/scoreA: 0.642257
2022-01-27T16:18:14 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T16:18:14 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:18:14 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.

WARNING 2022-01-27T16:22:35 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:22:35 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T16:23:13 | mmf.trainers.callbacks.logistics: progress: 400/2000, val/mami/cross_entropy: 0.4543, val/total_loss: 0.4543, val/mami/scoreA: 0.7924, val/mami/binary_f1: 0.8034, val/mami/roc_auc: 0.8711, num_updates: 400, epoch: 1, iterations: 400, max_updates: 2000, val_time: 44s 743ms, best_update: 400, best_iteration: 400, best_val/mami/scoreA: 0.792417
2022-01-27T16:23:31 | mmf.trainers.callbacks.checkpoint:

2022-01-27T16:27:30 | mmf.trainers.callbacks.logistics: progress: 600/2000, train/mami/cross_entropy: 0.5785, train/mami/cross_entropy/avg: 0.5966, train/total_loss: 0.5785, train/total_loss/avg: 0.5966, max mem: 7100.0, experiment: run, epoch: 1, num_updates: 600, iterations: 600, max_updates: 2000, lr: 0.00002, ups: 1.35, time: 37s 681ms, time_since_start: 15m 34s 341ms, eta: 18m 38s 400ms
2022-01-27T16:27:30 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T16:27:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:27:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when savi

...

WARNING 2022-01-27T16:41:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:41:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T16:42:16 | mmf.trainers.callbacks.logistics: progress: 1150/2000, val/mami/cross_entropy: 0.4164, val/total_loss: 0.4164, val/mami/scoreA: 0.8260, val/mami/binary_f1: 0.8448, val/mami/roc_auc: 0.9045, num_updates: 1150, epoch: 2, iterations: 1150, max_updates: 2000, val_time: 39s 802ms, best_update: 1050, best_iteration: 1050, best_val/mami/scoreA: 0.828481
2022-01-27T16:42:34 | mmf.trainers.callbacks.checkp

2022-01-27T16:47:12 | mmf.trainers.callbacks.logistics: progress: 1350/2000, train/mami/cross_entropy: 0.3073, train/mami/cross_entropy/avg: 0.4217, train/total_loss: 0.3073, train/total_loss/avg: 0.4217, max mem: 7100.0, experiment: run, epoch: 3, num_updates: 1350, iterations: 1350, max_updates: 2000, lr: 0.00001, ups: 1.47, time: 34s 786ms, time_since_start: 35m 15s 967ms, eta: 07m 59s 359ms
2022-01-27T16:47:12 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T16:47:19 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:47:19 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when s

2022-01-27T16:51:29 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T16:51:29 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:51:29 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T16:51:47 | mmf.trainers.callbacks.logistics: progress: 1550/2000, train/mami/cross_entropy: 0.2276, train/mami/cross_entropy/avg: 0.3872, train/total_loss: 0.2276, train/total_loss/avg: 0.3872, max mem: 7100.0, experiment: run, epoch: 3, num_updates: 1550, iterations: 1550, max_updates: 2000, lr: 0., ups: 1.39, tim

2022-01-27T16:57:42 | mmf.trainers.callbacks.logistics: progress: 1800/2000, train/mami/cross_entropy: 0.1939, train/mami/cross_entropy/avg: 0.3585, train/total_loss: 0.1939, train/total_loss/avg: 0.3585, max mem: 7100.0, experiment: run, epoch: 3, num_updates: 1800, iterations: 1800, max_updates: 2000, lr: 0., ups: 1.32, time: 38s 086ms, time_since_start: 45m 45s 841ms, eta: 02m 41s 488ms
2022-01-27T16:57:42 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T16:57:49 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T16:57:49 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving

2022-01-27T17:02:07 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:02:07 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T17:02:07 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T17:02:24 | mmf.trainers.callbacks.logistics: progress: 2000/2000, train/mami/cross_entropy: 0.1872, train/mami/cross_entropy/avg: 0.3377, train/total_loss: 0.1872, train/total_loss/avg: 0.3377, max mem: 7100.0, experiment: run, epoch: 4, num_updates: 2000, iterations: 2000, max_updates: 2000, lr: 0., ups: 1.47, tim

In [6]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_misogynous11.jsonl")

!mmf_run config="projects/mmf_transformer/configs/mami/defaults.yaml" \
        model="mmf_transformer" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_misogynous.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/mmf_transformer_misogynous \
        env.tensorboard_logdir=new_logs/fit/mmf_transformer_misogynous

2022-01-27 17:03:11.253779: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 17:03:11.253802: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.embeddings)

2022-01-27T17:03:47 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:03:47 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T17:03:47 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T17:04:04 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.6321, train/mami/cross_entropy/avg: 0.6321, train/total_loss: 0.6321, train/total_loss/avg: 0.6321, max mem: 7107.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0., ups: 1.43, time: 35s

2022-01-27T17:06:08 | mmf.trainers.callbacks.logistics: progress: 100/2000, val/mami/cross_entropy: 0.6443, val/total_loss: 0.6443, val/mami/scoreA: 0.6121, val/mami/binary_f1: 0.6458, val/mami/roc_auc: 0.6695, num_updates: 100, epoch: 1, iterations: 100, max_updates: 2000, val_time: 46s 947ms, best_update: 100, best_iteration: 100, best_val/mami/scoreA: 0.612064
2022-01-27T17:06:26 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:06:26 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-27T1

2022-01-27T17:08:03 | mmf.trainers.callbacks.logistics: progress: 200/2000, train/mami/cross_entropy: 0.6321, train/mami/cross_entropy/avg: 0.6393, train/total_loss: 0.6321, train/total_loss/avg: 0.6393, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 200, iterations: 200, max_updates: 2000, lr: 0.00001, ups: 1.43, time: 35s 362ms, time_since_start: 04m 34s 437ms, eta: 22m 29s 426ms
2022-01-27T17:08:03 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T17:08:10 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, cat

2022-01-27T17:10:13 | mmf.trainers.callbacks.logistics: progress: 250/2000, val/mami/cross_entropy: 0.4889, val/total_loss: 0.4889, val/mami/scoreA: 0.7780, val/mami/binary_f1: 0.7771, val/mami/roc_auc: 0.8530, num_updates: 250, epoch: 1, iterations: 250, max_updates: 2000, val_time: 44s 553ms, best_update: 250, best_iteration: 250, best_val/mami/scoreA: 0.777996
2022-01-27T17:10:31 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:10:31 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-27T1

...

2022-01-27T17:43:41 | mmf.trainers.callbacks.logistics: progress: 1600/2000, val/mami/cross_entropy: 0.5095, val/total_loss: 0.5095, val/mami/scoreA: 0.8394, val/mami/binary_f1: 0.8491, val/mami/roc_auc: 0.9120, num_updates: 1600, epoch: 3, iterations: 1600, max_updates: 2000, val_time: 35s 794ms, best_update: 1300, best_iteration: 1300, best_val/mami/scoreA: 0.844764
2022-01-27T17:43:59 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:43:59 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-27T17:45:42 | mmf.trainers.callbacks.logistics: progress: 1700/2000, train/mami/cross_entropy: 0.1110, train/mami/cross_entropy/avg: 0.2997, train/total_loss: 0.1110, train/total_loss/avg: 0.2997, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1700, iterations: 1700, max_updates: 2000, lr: 0., ups: 1.22, time: 41s 557ms, time_since_start: 42m 13s 173ms, eta: 04m 24s 308ms
2022-01-27T17:45:42 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T17:45:49 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, categ

2022-01-27T17:49:39 | mmf.trainers.callbacks.logistics: progress: 1850/2000, val/mami/cross_entropy: 0.5311, val/total_loss: 0.5311, val/mami/scoreA: 0.8436, val/mami/binary_f1: 0.8517, val/mami/roc_auc: 0.9125, num_updates: 1850, epoch: 4, iterations: 1850, max_updates: 2000, val_time: 32s 164ms, best_update: 1750, best_iteration: 1750, best_val/mami/scoreA: 0.847844
2022-01-27T17:49:57 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:49:57 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-27T17:51:33 | mmf.trainers.callbacks.logistics: progress: 1950/2000, train/mami/cross_entropy: 0.0977, train/mami/cross_entropy/avg: 0.2711, train/total_loss: 0.0977, train/total_loss/avg: 0.2711, max mem: 7108.0, experiment: run, epoch: 4, num_updates: 1950, iterations: 1950, max_updates: 2000, lr: 0., ups: 1.61, time: 31s 509ms, time_since_start: 48m 04s 611ms, eta: 33s 400ms
2022-01-27T17:51:33 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T17:51:40 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-27T17:53:33 | mmf.trainers.callbacks.logistics: progress: 2000/2000, val/mami/cross_entropy: 0.5378, val/total_loss: 0.5378, val/mami/scoreA: 0.8517, val/mami/binary_f1: 0.8582, val/mami/roc_auc: 0.9121, num_updates: 2000, epoch: 4, iterations: 2000, max_updates: 2000, val_time: 45s 932ms, best_update: 2000, best_iteration: 2000, best_val/mami/scoreA: 0.851713
2022-01-27T17:53:33 | mmf.trainers.core.training_loop: Stepping into final validation check
2022-01-27T17:53:33 | mmf.utils.checkpoint: Restoring checkpoint
2022-01-27T17:53:33 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-27T17:53:35 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:218: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T17:53:35 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_s

In [35]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_misogynous11.jsonl")

!mmf_run config="projects/vilbert/configs/mami/from_cc.yaml" \
        model="vilbert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_misogynous.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/vilbert_misogynous \
        env.tensorboard_logdir=new_logs/fit/vilbert_misogynous

2022-01-28 16:00:29.006074: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 16:00:29.006099: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T16:00:31 | mmf.utils.configuration: Overriding option config to projects/vilbert/configs/mami/from_cc.yaml
2022-01-28T16:00:31 | mmf.ut

2022-01-28T16:00:41 | mmf.trainers.mmf_trainer: Loading optimizer
2022-01-28T16:00:41 | mmf.trainers.mmf_trainer: Loading metrics
()
2022-01-28T16:00:41 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-28T16:00:43 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-28T16:00:43 | mmf: Key distributed is not present in registry, returning default value of None
WARNING 2022-01-28T16:00:43 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-28T16:00:43 | mmf: Key distributed is not present in registry, returning default value of None
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.embeddings.word_embeddings.weight from model.bert.embeddings.word_embeddings.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.embeddings.position_embeddings.weight from model.bert.embeddings.position_embeddings.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying mo

2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.LayerNorm.bias from model.bert.encoder.layer.2.attention.output.LayerNorm.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.intermediate.dense.weight from model.bert.encoder.layer.2.intermediate.dense.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.intermediate.dense.bias from model.bert.encoder.layer.2.intermediate.dense.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.dense.weight from model.bert.encoder.layer.2.output.dense.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.dense.bias from model.bert.encoder.layer.2.output.dense.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.LayerNorm.weight from model.bert.encoder.layer.2.output.LayerNorm.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Co

2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.output.dense.weight from model.bert.encoder.layer.6.attention.output.dense.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.output.dense.bias from model.bert.encoder.layer.6.attention.output.dense.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.output.LayerNorm.weight from model.bert.encoder.layer.6.attention.output.LayerNorm.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.output.LayerNorm.bias from model.bert.encoder.layer.6.attention.output.LayerNorm.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.intermediate.dense.weight from model.bert.encoder.layer.6.intermediate.dense.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.intermediate.dense.bias from model.bert.encoder.layer.6.intermedia

2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.key.bias from model.bert.encoder.layer.10.attention.self.key.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.value.weight from model.bert.encoder.layer.10.attention.self.value.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.value.bias from model.bert.encoder.layer.10.attention.self.value.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.output.dense.weight from model.bert.encoder.layer.10.attention.output.dense.weight
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.output.dense.bias from model.bert.encoder.layer.10.attention.output.dense.bias
2022-01-28T16:00:43 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.output.LayerNorm.weight from model.bert.encoder.layer.10.attention.output

...

2022-01-28T16:54:01 | mmf.trainers.callbacks.logistics: progress: 1650/2000, train/mami/cross_entropy: 0.2023, train/mami/cross_entropy/avg: 0.3353, train/total_loss: 0.2023, train/total_loss/avg: 0.3353, max mem: 7253.0, experiment: run, epoch: 3, num_updates: 1650, iterations: 1650, max_updates: 2000, lr: 0.00001, ups: 1.61, time: 31s 412ms, time_since_start: 53m 19s 912ms, eta: 03m 53s 081ms
2022-01-28T16:54:01 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T16:54:10 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-28T16:57:33 | mmf.trainers.callbacks.logistics: progress: 1750/2000, train/mami/cross_entropy: 0.1533, train/mami/cross_entropy/avg: 0.3233, train/total_loss: 0.1533, train/total_loss/avg: 0.3233, max mem: 7253.0, experiment: run, epoch: 3, num_updates: 1750, iterations: 1750, max_updates: 2000, lr: 0., ups: 0.93, time: 54s 239ms, time_since_start: 56m 51s 458ms, eta: 04m 47s 467ms
2022-01-28T16:57:33 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T16:57:41 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T17:00:56 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.1101, train/mami/cross_entropy/avg: 0.3106, train/total_loss: 0.1101, train/total_loss/avg: 0.3106, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 0.91, time: 55s 450ms, time_since_start: 01h 15s 086ms, eta: 02m 56s 333ms
2022-01-28T17:00:56 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T17:01:05 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T17:04:11 | mmf.trainers.callbacks.logistics: progress: 1950/2000, train/mami/cross_entropy: 0.0901, train/mami/cross_entropy/avg: 0.2953, train/total_loss: 0.0901, train/total_loss/avg: 0.2953, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 1950, iterations: 1950, max_updates: 2000, lr: 0., ups: 1.02, time: 49s 178ms, time_since_start: 01h 03m 29s 831ms, eta: 52s 129ms
2022-01-28T17:04:11 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T17:04:20 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

100%|███████████████████████████████████████████| 63/63 [00:08<00:00,  7.59it/s]
2022-01-28T17:06:55 | mmf.trainers.callbacks.logistics: progress: 1200/2000, val/mami/cross_entropy: 0.3707, val/total_loss: 0.3707, val/mami/scoreA: 0.8443, val/mami/binary_f1: 0.8547, val/mami/roc_auc: 0.9188
2022-01-28T17:06:55 | mmf.trainers.callbacks.logistics: Finished run in 01h 06m 13s 228ms


## shaming

In [4]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_shaming11.jsonl")

!mmf_run config="projects/visual_bert/configs/mami/from_coco.yaml" \
        model="visual_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        checkpoint.resume_zoo=visual_bert.pretrained.cc.full \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_shaming.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/shaming_individual \
        env.tensorboard_logdir=new_logs/fit/shaming_individual_lr_testing

2022-01-28 07:10:37.972444: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 07:10:37.972468: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T07:10:45 | mmf.utils.configuration: Overriding option config to projects/visual_bert/configs/mami/from_coco.yaml
2022-01-28T07:10:45 | 

2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.0.output.dense.bias from model.bert.encoder.layer.0.output.dense.bias
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.0.output.LayerNorm.weight from model.bert.encoder.layer.0.output.LayerNorm.weight
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.0.output.LayerNorm.bias from model.bert.encoder.layer.0.output.LayerNorm.bias
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.self.query.weight from model.bert.encoder.layer.1.attention.self.query.weight
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.self.query.bias from model.bert.encoder.layer.1.attention.self.query.bias
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.self.key.weight from model.bert.encoder.layer.1.attention.self.key.weight
2022-01-28T07:11:06 | mmf.utils.checkpoint: Co

2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.query.bias from model.bert.encoder.layer.7.attention.self.query.bias
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.key.weight from model.bert.encoder.layer.7.attention.self.key.weight
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.key.bias from model.bert.encoder.layer.7.attention.self.key.bias
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.value.weight from model.bert.encoder.layer.7.attention.self.value.weight
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.value.bias from model.bert.encoder.layer.7.attention.self.value.bias
2022-01-28T07:11:06 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.output.dense.weight from model.bert.encoder.layer.7.attention.output.dense.weight
2022-01-28T07:

                (dropout): Dropout(p=0.1, inplace=False)
              )
            )
            (intermediate): BertIntermediate(
              (dense): Linear(in_features=768, out_features=3072, bias=True)
            )
            (output): BertOutput(
              (dense): Linear(in_features=3072, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
          )
          (5): BertLayerJit(
            (attention): BertAttentionJit(
              (self): BertSelfAttentionJit(
                (query): Linear(in_features=768, out_features=768, bias=True)
                (key): Linear(in_features=768, out_features=768, bias=True)
                (value): Linear(in_features=768, out_features=768, bias=True)
                (dropout): Dropout(p=0.1, inplace=False)
              )
              (output): BertSelfOutput(
                (dense): Linear(in_feature

2022-01-28T07:11:21 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T07:11:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T07:11:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T07:11:32 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.1134, train/mami/cross_entropy/avg: 0.1134, train/total_loss: 0.1134, train/total_loss/avg: 0.1134, max mem: 5481.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0.00001, ups: 2.00, time

...

2022-01-28T07:37:48 | mmf.trainers.callbacks.logistics: progress: 1550/2000, train/mami/cross_entropy: 0.2085, train/mami/cross_entropy/avg: 0.2917, train/total_loss: 0.2085, train/total_loss/avg: 0.2917, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1550, iterations: 1550, max_updates: 2000, lr: 0.00001, ups: 1.79, time: 28s 151ms, time_since_start: 26m 45s 699ms, eta: 04m 28s 563ms
2022-01-28T07:37:48 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:37:55 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-28T07:39:33 | mmf.trainers.callbacks.logistics: progress: 1650/2000, train/mami/cross_entropy: 0.1981, train/mami/cross_entropy/avg: 0.2763, train/total_loss: 0.1981, train/total_loss/avg: 0.2763, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1650, iterations: 1650, max_updates: 2000, lr: 0.00001, ups: 1.85, time: 27s 707ms, time_since_start: 28m 30s 295ms, eta: 03m 25s 587ms
2022-01-28T07:39:33 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:39:40 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-28T07:41:20 | mmf.trainers.callbacks.logistics: progress: 1750/2000, train/mami/cross_entropy: 0.1817, train/mami/cross_entropy/avg: 0.2640, train/total_loss: 0.1817, train/total_loss/avg: 0.2640, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1750, iterations: 1750, max_updates: 2000, lr: 0., ups: 1.79, time: 28s 156ms, time_since_start: 30m 17s 727ms, eta: 02m 29s 231ms
2022-01-28T07:41:20 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:41:28 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T07:43:07 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.1356, train/mami/cross_entropy/avg: 0.2522, train/total_loss: 0.1356, train/total_loss/avg: 0.2522, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 1.79, time: 28s 487ms, time_since_start: 32m 04s 189ms, eta: 01m 30s 590ms
2022-01-28T07:43:07 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:43:14 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T07:44:57 | mmf.trainers.callbacks.logistics: progress: 1950/2000, train/mami/cross_entropy: 0.0676, train/mami/cross_entropy/avg: 0.2420, train/total_loss: 0.0676, train/total_loss/avg: 0.2420, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1950, iterations: 1950, max_updates: 2000, lr: 0., ups: 1.72, time: 29s 278ms, time_since_start: 33m 54s 045ms, eta: 31s 034ms
2022-01-28T07:44:57 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:45:04 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarni

In [ ]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_shaming11.jsonl")

!mmf_run config="projects/others/late_fusion/mami/defaults.yaml" \
        model="late_fusion" \
        dataset=mami \
        checkpoint.max_to_keep=1 \
        run_type=train_val \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_shaming.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/late_fusion_shaming \
        env.tensorboard_logdir=new_logs/fit/late_fusion_shaming_lr_testing

In [ ]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_shaming11.jsonl")

!mmf_run config="projects/mmbt/configs/mami/with_features.yaml" \
        model="mmbt" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_shaming.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/mmbt_shaming \
        env.tensorboard_logdir=new_logs/fit/mmbt_shaming_lr_testing

In [36]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_shaming11.jsonl")

!mmf_run config="projects/vilbert/configs/mami/from_cc.yaml" \
        model="vilbert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_shaming.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/vilbert_shaming \
        env.tensorboard_logdir=new_logs/fit/vilbert_shaming

2022-01-28 17:06:57.749011: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 17:06:57.749035: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T17:07:05 | mmf.utils.configuration: Overriding option config to projects/vilbert/configs/mami/from_cc.yaml
2022-01-28T17:07:05 | mmf.ut

2022-01-28T17:07:21 | mmf.trainers.mmf_trainer: Loading optimizer
2022-01-28T17:07:21 | mmf.trainers.mmf_trainer: Loading metrics
()
2022-01-28T17:07:21 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-28T17:07:29 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-28T17:07:29 | mmf: Key distributed is not present in registry, returning default value of None
WARNING 2022-01-28T17:07:29 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-28T17:07:29 | mmf: Key distributed is not present in registry, returning default value of None
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.embeddings.word_embeddings.weight from model.bert.embeddings.word_embeddings.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.embeddings.position_embeddings.weight from model.bert.embeddings.position_embeddings.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying mo

2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.query.weight from model.bert.encoder.layer.6.attention.self.query.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.query.bias from model.bert.encoder.layer.6.attention.self.query.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.key.weight from model.bert.encoder.layer.6.attention.self.key.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.key.bias from model.bert.encoder.layer.6.attention.self.key.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.value.weight from model.bert.encoder.layer.6.attention.self.value.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.value.bias from model.bert.encoder.layer.6.attention.self.value.bias
2022-01-28T17:07:2

2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.output.LayerNorm.bias from model.bert.encoder.layer.9.output.LayerNorm.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.query.weight from model.bert.encoder.layer.10.attention.self.query.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.query.bias from model.bert.encoder.layer.10.attention.self.query.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.key.weight from model.bert.encoder.layer.10.attention.self.key.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.key.bias from model.bert.encoder.layer.10.attention.self.key.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.value.weight from model.bert.encoder.layer.10.attention.self.value.weight
2022-01-28T17:07

2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.v_layer.1.output.LayerNorm.bias from model.bert.encoder.v_layer.1.output.LayerNorm.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.v_layer.2.attention.self.query.weight from model.bert.encoder.v_layer.2.attention.self.query.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.v_layer.2.attention.self.query.bias from model.bert.encoder.v_layer.2.attention.self.query.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.v_layer.2.attention.self.key.weight from model.bert.encoder.v_layer.2.attention.self.key.weight
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.v_layer.2.attention.self.key.bias from model.bert.encoder.v_layer.2.attention.self.key.bias
2022-01-28T17:07:29 | mmf.utils.checkpoint: Copying model.bert.encoder.v_layer.2.attention.self.value.weight from model.bert.encoder.v_layer.2.attention.self.value.weight
20

...

2022-01-28T17:58:50 | mmf.trainers.callbacks.logistics: progress: 1600/2000, train/mami/cross_entropy: 0.1531, train/mami/cross_entropy/avg: 0.3001, train/total_loss: 0.1531, train/total_loss/avg: 0.3001, max mem: 7253.0, experiment: run, epoch: 3, num_updates: 1600, iterations: 1600, max_updates: 2000, lr: 0.00001, ups: 1.00, time: 50s 203ms, time_since_start: 51m 28s 981ms, eta: 07m 05s 726ms
2022-01-28T17:58:50 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T17:58:58 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-28T18:01:26 | mmf.trainers.callbacks.logistics: progress: 1700/2000, train/mami/cross_entropy: 0.1308, train/mami/cross_entropy/avg: 0.2909, train/total_loss: 0.1308, train/total_loss/avg: 0.2909, max mem: 7253.0, experiment: run, epoch: 3, num_updates: 1700, iterations: 1700, max_updates: 2000, lr: 0., ups: 1.04, time: 48s 297ms, time_since_start: 54m 05s 059ms, eta: 05m 07s 175ms
2022-01-28T18:01:26 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:01:34 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T18:04:24 | mmf.trainers.callbacks.logistics: progress: 1800/2000, train/mami/cross_entropy: 0.1197, train/mami/cross_entropy/avg: 0.2825, train/total_loss: 0.1197, train/total_loss/avg: 0.2825, max mem: 7253.0, experiment: run, epoch: 3, num_updates: 1800, iterations: 1800, max_updates: 2000, lr: 0., ups: 1.09, time: 46s 498ms, time_since_start: 57m 03s 422ms, eta: 03m 17s 155ms
2022-01-28T18:04:24 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:04:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T18:07:15 | mmf.trainers.callbacks.logistics: progress: 1900/2000, train/mami/cross_entropy: 0.0906, train/mami/cross_entropy/avg: 0.2683, train/total_loss: 0.0906, train/total_loss/avg: 0.2683, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 1900, iterations: 1900, max_updates: 2000, lr: 0., ups: 1.67, time: 30s 808ms, time_since_start: 59m 53s 662ms, eta: 01m 05s 313ms
2022-01-28T18:07:15 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:07:23 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T18:10:19 | mmf.trainers.callbacks.logistics: progress: 2000/2000, train/mami/cross_entropy: 0.0906, train/mami/cross_entropy/avg: 0.2616, train/total_loss: 0.0906, train/total_loss/avg: 0.2616, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 2000, iterations: 2000, max_updates: 2000, lr: 0., ups: 1.39, time: 36s 189ms, time_since_start: 01h 02m 58s 106ms, eta: 0ms
2022-01-28T18:10:19 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:10:27 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning

## stereotype

In [2]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_stereotype11.jsonl")

!mmf_run config="projects/others/late_fusion/mami/defaults.yaml" \
        model="late_fusion" \
        dataset=mami \
        checkpoint.max_to_keep=1 \
        run_type=train_val \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_stereotype.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/late_fusion_stereotype \
        env.tensorboard_logdir=new_logs/fit/late_fusion_stereotype

2022-01-27 22:46:50.387465: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 22:46:50.387488: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2022-01-27T22:46:58 | mmf.utils.configuration: Overriding option config to projects/others/late_fusion/mami/defaults.yaml
2022-01-27T22:46:58 | mmf.utils.configuration: Overriding option model to late_fusion
2022-01-27T22:46:58 | mmf.utils.configuration: Overriding option datasets to mami
2022-01-27T22:46:58 | mmf.utils.configuration: Overriding option checkpoint.max_to_keep to 1
2022-01-27T22:46:58 | mmf.utils.configuration: Overriding option run_type to train_val
2022-01-27T22:46:58 | mmf.utils.configuration: Overriding option training.tensorboard to True
2022-01-27T22:46:58 | mmf.utils.configuration: O

2022-01-27T22:47:15 | mmf.utils.general: Total Parameters: 170980676. Trained Parameters: 170980676
2022-01-27T22:47:15 | mmf.trainers.core.training_loop: Starting training...
2022-01-27T22:47:34 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T22:47:34 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T22:47:34 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T22:47:54 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.7301, train/mami/cross_entropy/avg: 0.7301, trai

2022-01-27T22:52:50 | mmf.trainers.callbacks.logistics: progress: 200/2000, val/mami/cross_entropy: 0.6108, val/total_loss: 0.6108, val/mami/scoreA: 0.6094, val/mami/binary_f1: 0.4633, val/mami/roc_auc: 0.6936, num_updates: 200, epoch: 1, iterations: 200, max_updates: 2000, val_time: 45s 586ms, best_update: 200, best_iteration: 200, best_val/mami/scoreA: 0.609359
2022-01-27T22:53:08 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T22:53:08 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T22:53:08 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.

WARNING 2022-01-27T22:57:34 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T22:57:34 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T22:58:02 | mmf.trainers.callbacks.logistics: progress: 400/2000, val/mami/cross_entropy: 0.8262, val/total_loss: 0.8262, val/mami/scoreA: 0.5820, val/mami/binary_f1: 0.5281, val/mami/roc_auc: 0.7694, num_updates: 400, epoch: 1, iterations: 400, max_updates: 2000, val_time: 34s 129ms, best_update: 350, best_iteration: 350, best_val/mami/scoreA: 0.682713
2022-01-27T22:58:20 | mmf.trainers.callbacks.checkpoint:

2022-01-27T23:02:25 | mmf.trainers.callbacks.logistics: progress: 600/2000, train/mami/cross_entropy: 0.4473, train/mami/cross_entropy/avg: 0.5268, train/total_loss: 0.4473, train/total_loss/avg: 0.5268, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 600, iterations: 600, max_updates: 2000, lr: 0.00005, ups: 1.28, time: 39s 859ms, time_since_start: 15m 09s 983ms, eta: 19m 43s 027ms
2022-01-27T23:02:25 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T23:02:32 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:02:32 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when savi

...

WARNING 2022-01-27T23:16:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:16:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T23:17:07 | mmf.trainers.callbacks.logistics: progress: 1150/2000, val/mami/cross_entropy: 0.4691, val/total_loss: 0.4691, val/mami/scoreA: 0.6972, val/mami/binary_f1: 0.5436, val/mami/roc_auc: 0.8101, num_updates: 1150, epoch: 2, iterations: 1150, max_updates: 2000, val_time: 36s 670ms, best_update: 950, best_iteration: 950, best_val/mami/scoreA: 0.711432
2022-01-27T23:17:25 | mmf.trainers.callbacks.checkpoi

2022-01-27T23:21:12 | mmf.trainers.callbacks.logistics: progress: 1350/2000, train/mami/cross_entropy: 0.3909, train/mami/cross_entropy/avg: 0.4555, train/total_loss: 0.3909, train/total_loss/avg: 0.4555, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1350, iterations: 1350, max_updates: 2000, lr: 0.00002, ups: 1.43, time: 35s 855ms, time_since_start: 33m 57s 103ms, eta: 08m 14s 082ms
2022-01-27T23:21:12 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T23:21:19 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:21:19 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when s

2022-01-27T23:25:50 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T23:25:50 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:25:50 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T23:26:05 | mmf.trainers.callbacks.logistics: progress: 1550/2000, train/mami/cross_entropy: 0.3445, train/mami/cross_entropy/avg: 0.4295, train/total_loss: 0.3445, train/total_loss/avg: 0.4295, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1550, iterations: 1550, max_updates: 2000, lr: 0.00001, ups: 1.52

2022-01-27T23:30:46 | mmf.trainers.callbacks.logistics: progress: 1700/2000, val/mami/cross_entropy: 0.5326, val/total_loss: 0.5326, val/mami/scoreA: 0.7202, val/mami/binary_f1: 0.5887, val/mami/roc_auc: 0.7962, num_updates: 1700, epoch: 3, iterations: 1700, max_updates: 2000, val_time: 46s 418ms, best_update: 1700, best_iteration: 1700, best_val/mami/scoreA: 0.720190
2022-01-27T23:31:04 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T23:31:04 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:31:04 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warn

WARNING 2022-01-27T23:35:18 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:35:18 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T23:35:45 | mmf.trainers.callbacks.logistics: progress: 1900/2000, val/mami/cross_entropy: 0.5330, val/total_loss: 0.5330, val/mami/scoreA: 0.7160, val/mami/binary_f1: 0.5822, val/mami/roc_auc: 0.8004, num_updates: 1900, epoch: 4, iterations: 1900, max_updates: 2000, val_time: 34s 091ms, best_update: 1750, best_iteration: 1750, best_val/mami/scoreA: 0.725643
2022-01-27T23:36:03 | mmf.trainers.callbacks.checkp

In [3]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_stereotype11.jsonl")

!mmf_run config="projects/mmf_transformer/configs/mami/defaults.yaml" \
        model="mmf_transformer" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_stereotype.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/mmf_transformer_stereotype \
        env.tensorboard_logdir=new_logs/fit/mmf_transformer_stereotype

2022-01-27 23:38:25.733616: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 23:38:25.733641: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.embeddings)

2022-01-27T23:39:01 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T23:39:01 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T23:39:01 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T23:39:27 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.7001, train/mami/cross_entropy/avg: 0.7001, train/total_loss: 0.7001, train/total_loss/avg: 0.7001, max mem: 7107.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0.00001, ups: 1.16, time

2022-01-27T23:41:40 | mmf.trainers.callbacks.logistics: progress: 100/2000, val/mami/cross_entropy: 0.5621, val/total_loss: 0.5621, val/mami/scoreA: 0.4269, val/mami/binary_f1: 0.0075, val/mami/roc_auc: 0.6578, num_updates: 100, epoch: 1, iterations: 100, max_updates: 2000, val_time: 47s 490ms, best_update: 100, best_iteration: 100, best_val/mami/scoreA: 0.426942
2022-01-27T23:41:58 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T23:41:58 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-27T2

2022-01-27T23:43:43 | mmf.trainers.callbacks.logistics: progress: 200/2000, train/mami/cross_entropy: 0.4396, train/mami/cross_entropy/avg: 0.5146, train/total_loss: 0.4396, train/total_loss/avg: 0.5146, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 200, iterations: 200, max_updates: 2000, lr: 0.00002, ups: 1.39, time: 36s 596ms, time_since_start: 04m 59s 957ms, eta: 23m 16s 511ms
2022-01-27T23:43:43 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T23:43:50 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, cat

2022-01-27T23:46:02 | mmf.trainers.callbacks.logistics: progress: 250/2000, val/mami/cross_entropy: 0.6432, val/total_loss: 0.6432, val/mami/scoreA: 0.6609, val/mami/binary_f1: 0.5429, val/mami/roc_auc: 0.7625, num_updates: 250, epoch: 1, iterations: 250, max_updates: 2000, val_time: 52s 289ms, best_update: 250, best_iteration: 250, best_val/mami/scoreA: 0.660938
2022-01-27T23:46:19 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T23:46:19 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-27T2

...

2022-01-28T00:20:28 | mmf.trainers.callbacks.logistics: progress: 1600/2000, val/mami/cross_entropy: 0.7101, val/total_loss: 0.7101, val/mami/scoreA: 0.7165, val/mami/binary_f1: 0.5781, val/mami/roc_auc: 0.8072, num_updates: 1600, epoch: 3, iterations: 1600, max_updates: 2000, val_time: 37s 291ms, best_update: 1200, best_iteration: 1200, best_val/mami/scoreA: 0.718136
2022-01-28T00:20:46 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T00:20:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-28T00:22:37 | mmf.trainers.callbacks.logistics: progress: 1700/2000, train/mami/cross_entropy: 0.2529, train/mami/cross_entropy/avg: 0.3414, train/total_loss: 0.2529, train/total_loss/avg: 0.3414, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1700, iterations: 1700, max_updates: 2000, lr: 0., ups: 1.39, time: 36s 747ms, time_since_start: 43m 54s 063ms, eta: 03m 53s 717ms
2022-01-28T00:22:37 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T00:22:44 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, categ

2022-01-28T00:24:29 | mmf.trainers.callbacks.logistics: progress: 1750/2000, val/mami/cross_entropy: 0.6716, val/total_loss: 0.6716, val/mami/scoreA: 0.7132, val/mami/binary_f1: 0.5758, val/mami/roc_auc: 0.8083, num_updates: 1750, epoch: 3, iterations: 1750, max_updates: 2000, val_time: 35s 129ms, best_update: 1650, best_iteration: 1650, best_val/mami/scoreA: 0.723490
2022-01-28T00:24:46 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T00:24:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-28T00:26:26 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.1830, train/mami/cross_entropy/avg: 0.3267, train/total_loss: 0.1830, train/total_loss/avg: 0.3267, max mem: 7108.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 1.35, time: 37s 028ms, time_since_start: 47m 43s 029ms, eta: 01m 57s 750ms
2022-01-28T00:26:26 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
2022-01-28T00:28:34 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T00:28:34 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by sett

2022-01-28T00:30:13 | mmf.trainers.callbacks.logistics: progress: 2000/2000, train/mami/cross_entropy: 0.1430, train/mami/cross_entropy/avg: 0.3122, train/total_loss: 0.1430, train/total_loss/avg: 0.3122, max mem: 7108.0, experiment: run, epoch: 4, num_updates: 2000, iterations: 2000, max_updates: 2000, lr: 0., ups: 1.35, time: 37s 438ms, time_since_start: 51m 30s 102ms, eta: 0ms
2022-01-28T00:30:13 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T00:30:20 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWa

In [4]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_stereotype11.jsonl")

!mmf_run config="projects/visual_bert/configs/mami/from_coco.yaml" \
        model="visual_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        checkpoint.resume_zoo=visual_bert.pretrained.cc.full \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_stereotype.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/stereotype_individual \
        env.tensorboard_logdir=new_logs/fit/stereotype_individual

2022-01-28 00:31:09.156133: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 00:31:09.156158: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T00:31:11 | mmf.utils.configuration: Overriding option config to projects/visual_bert/configs/mami/from_coco.yaml
2022-01-28T00:31:11 | 

2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.dense.weight from model.bert.encoder.layer.2.output.dense.weight
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.dense.bias from model.bert.encoder.layer.2.output.dense.bias
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.LayerNorm.weight from model.bert.encoder.layer.2.output.LayerNorm.weight
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.output.LayerNorm.bias from model.bert.encoder.layer.2.output.LayerNorm.bias
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.self.query.weight from model.bert.encoder.layer.3.attention.self.query.weight
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.self.query.bias from model.bert.encoder.layer.3.attention.self.query.bias
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.

2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.intermediate.dense.bias from model.bert.encoder.layer.8.intermediate.dense.bias
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.dense.weight from model.bert.encoder.layer.8.output.dense.weight
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.dense.bias from model.bert.encoder.layer.8.output.dense.bias
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.LayerNorm.weight from model.bert.encoder.layer.8.output.LayerNorm.weight
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.LayerNorm.bias from model.bert.encoder.layer.8.output.LayerNorm.bias
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.attention.self.query.weight from model.bert.encoder.layer.9.attention.self.query.weight
2022-01-28T00:31:27 | mmf.utils.checkpoint: Copying model.bert

2022-01-28T00:31:42 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T00:31:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T00:31:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T00:31:50 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.4417, train/mami/cross_entropy/avg: 0.4417, train/total_loss: 0.4417, train/total_loss/avg: 0.4417, max mem: 5481.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0.00001, ups: 2.17, time

2022-01-28T00:34:08 | mmf.trainers.callbacks.logistics: progress: 150/2000, train/mami/cross_entropy: 0.4564, train/mami/cross_entropy/avg: 0.4664, train/total_loss: 0.4564, train/total_loss/avg: 0.4664, max mem: 5484.0, experiment: run, epoch: 1, num_updates: 150, iterations: 150, max_updates: 2000, lr: 0.00002, ups: 1.92, time: 26s 845ms, time_since_start: 02m 44s 053ms, eta: 17m 32s 880ms
2022-01-28T00:34:08 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T00:34:15 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=Use

...

2022-01-28T00:59:29 | mmf.trainers.callbacks.logistics: progress: 1650/2000, train/mami/cross_entropy: 0.2505, train/mami/cross_entropy/avg: 0.3311, train/total_loss: 0.2505, train/total_loss/avg: 0.3311, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1650, iterations: 1650, max_updates: 2000, lr: 0.00001, ups: 1.92, time: 26s 544ms, time_since_start: 28m 04s 806ms, eta: 03m 16s 961ms
2022-01-28T00:59:29 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T00:59:36 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-28T01:01:13 | mmf.trainers.callbacks.logistics: progress: 1750/2000, train/mami/cross_entropy: 0.2332, train/mami/cross_entropy/avg: 0.3181, train/total_loss: 0.2332, train/total_loss/avg: 0.3181, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1750, iterations: 1750, max_updates: 2000, lr: 0., ups: 1.92, time: 26s 517ms, time_since_start: 29m 48s 836ms, eta: 02m 20s 540ms
2022-01-28T01:01:13 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T01:01:20 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T01:02:56 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.2048, train/mami/cross_entropy/avg: 0.3071, train/total_loss: 0.2048, train/total_loss/avg: 0.3071, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 1.85, time: 27s 798ms, time_since_start: 31m 32s 582ms, eta: 01m 28s 399ms
2022-01-28T01:02:56 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T01:03:04 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T01:04:39 | mmf.trainers.callbacks.logistics: progress: 1950/2000, train/mami/cross_entropy: 0.1587, train/mami/cross_entropy/avg: 0.2948, train/total_loss: 0.1587, train/total_loss/avg: 0.2948, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1950, iterations: 1950, max_updates: 2000, lr: 0., ups: 1.92, time: 26s 084ms, time_since_start: 33m 15s 133ms, eta: 27s 649ms
2022-01-28T01:04:39 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T01:04:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarni

100%|███████████████████████████████████████████| 63/63 [00:07<00:00,  8.64it/s]
2022-01-28T01:06:16 | mmf.trainers.callbacks.logistics: progress: 1350/2000, val/mami/cross_entropy: 0.5933, val/total_loss: 0.5933, val/mami/scoreA: 0.7219, val/mami/binary_f1: 0.5823, val/mami/roc_auc: 0.8173
2022-01-28T01:06:16 | mmf.trainers.callbacks.logistics: Finished run in 34m 52s 273ms


## objectification

In [7]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_objectification11.jsonl")

!mmf_run config="projects/others/concat_bert/mami/defaults.yaml" \
        model="concat_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_objectification.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/concat_bert_objectification \
        env.tensorboard_logdir=new_logs/fit/concat_bert_objectification

2022-01-27 17:53:47.017296: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 17:53:47.017320: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2022-01-27T17:53:49 | mmf.utils.configuration: Overriding option config to projects/others/concat_bert/mami/defaults.yaml
2022-01-27T17:53:49 | mmf.utils.configuration: Overriding option model to concat_bert
2022-01-27T17:53:49 | mmf.utils.configuration: Overriding option datasets to mami
2022-01-27T17:53:49 | mmf.utils.configuration: Overriding option run_type to train_val
2022-01-27T17:53:49 | mmf.utils.configuration: Overriding option checkpoint.max_to_keep to 1
2022-01-27T17:53:49 | mmf.utils.configuration: Overriding option training.tensorboard to True
2022-01-27T17:53:49 | mmf.utils.configuration: O

2022-01-27T17:54:03 | mmf.utils.general: Total Parameters: 170384706. Trained Parameters: 170384706
2022-01-27T17:54:03 | mmf.trainers.core.training_loop: Starting training...
2022-01-27T17:54:21 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:54:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T17:54:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T17:54:30 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.7529, train/mami/cross_entropy/avg: 0.7529, trai

2022-01-27T17:59:19 | mmf.trainers.callbacks.logistics: progress: 200/2000, val/mami/cross_entropy: 0.6012, val/total_loss: 0.6012, val/mami/scoreA: 0.6221, val/mami/binary_f1: 0.4388, val/mami/roc_auc: 0.7256, num_updates: 200, epoch: 1, iterations: 200, max_updates: 2000, val_time: 42s 207ms, best_update: 200, best_iteration: 200, best_val/mami/scoreA: 0.622111
2022-01-27T17:59:37 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T17:59:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T17:59:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.

WARNING 2022-01-27T18:03:45 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:03:45 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T18:04:23 | mmf.trainers.callbacks.logistics: progress: 400/2000, val/mami/cross_entropy: 0.4865, val/total_loss: 0.4865, val/mami/scoreA: 0.6986, val/mami/binary_f1: 0.5238, val/mami/roc_auc: 0.7757, num_updates: 400, epoch: 1, iterations: 400, max_updates: 2000, val_time: 45s 362ms, best_update: 400, best_iteration: 400, best_val/mami/scoreA: 0.698614
2022-01-27T18:04:41 | mmf.trainers.callbacks.checkpoint:

2022-01-27T18:08:59 | mmf.trainers.callbacks.logistics: progress: 600/2000, train/mami/cross_entropy: 0.4801, train/mami/cross_entropy/avg: 0.5354, train/total_loss: 0.4801, train/total_loss/avg: 0.5354, max mem: 7100.0, experiment: run, epoch: 1, num_updates: 600, iterations: 600, max_updates: 2000, lr: 0.00002, ups: 1.39, time: 36s 162ms, time_since_start: 14m 55s 682ms, eta: 17m 53s 312ms
2022-01-27T18:08:59 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T18:09:05 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:09:05 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when savi

...

WARNING 2022-01-27T18:22:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:22:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T18:23:13 | mmf.trainers.callbacks.logistics: progress: 1150/2000, val/mami/cross_entropy: 0.3997, val/total_loss: 0.3997, val/mami/scoreA: 0.7507, val/mami/binary_f1: 0.6183, val/mami/roc_auc: 0.8653, num_updates: 1150, epoch: 2, iterations: 1150, max_updates: 2000, val_time: 33s 688ms, best_update: 950, best_iteration: 950, best_val/mami/scoreA: 0.762517
2022-01-27T18:23:31 | mmf.trainers.callbacks.checkpoi

2022-01-27T18:27:25 | mmf.trainers.callbacks.logistics: progress: 1350/2000, train/mami/cross_entropy: 0.3718, train/mami/cross_entropy/avg: 0.4192, train/total_loss: 0.3718, train/total_loss/avg: 0.4192, max mem: 7100.0, experiment: run, epoch: 3, num_updates: 1350, iterations: 1350, max_updates: 2000, lr: 0.00001, ups: 1.52, time: 33s 746ms, time_since_start: 33m 21s 550ms, eta: 07m 45s 025ms
2022-01-27T18:27:25 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T18:27:31 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:27:31 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when s

2022-01-27T18:31:47 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T18:31:47 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:31:47 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T18:32:05 | mmf.trainers.callbacks.logistics: progress: 1550/2000, train/mami/cross_entropy: 0.2708, train/mami/cross_entropy/avg: 0.3942, train/total_loss: 0.2708, train/total_loss/avg: 0.3942, max mem: 7100.0, experiment: run, epoch: 3, num_updates: 1550, iterations: 1550, max_updates: 2000, lr: 0., ups: 1.43, tim

2022-01-27T18:36:15 | mmf.trainers.callbacks.logistics: progress: 1700/2000, val/mami/cross_entropy: 0.3838, val/total_loss: 0.3838, val/mami/scoreA: 0.7624, val/mami/binary_f1: 0.6330, val/mami/roc_auc: 0.8678, num_updates: 1700, epoch: 3, iterations: 1700, max_updates: 2000, val_time: 35s 235ms, best_update: 1250, best_iteration: 1250, best_val/mami/scoreA: 0.775379
2022-01-27T18:36:33 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T18:36:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:36:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warn

WARNING 2022-01-27T18:40:25 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:40:25 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T18:40:55 | mmf.trainers.callbacks.logistics: progress: 1900/2000, val/mami/cross_entropy: 0.3857, val/total_loss: 0.3857, val/mami/scoreA: 0.7628, val/mami/binary_f1: 0.6348, val/mami/roc_auc: 0.8691, num_updates: 1900, epoch: 4, iterations: 1900, max_updates: 2000, val_time: 36s 520ms, best_update: 1250, best_iteration: 1250, best_val/mami/scoreA: 0.775379
2022-01-27T18:41:13 | mmf.trainers.callbacks.checkp

In [8]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_objectification11.jsonl")

!mmf_run config="projects/mmf_transformer/configs/mami/defaults.yaml" \
        model="mmf_transformer" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_objectification.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/mmf_transformer_objectification \
        env.tensorboard_logdir=new_logs/fit/mmf_transformer_objectification

2022-01-27 18:43:33.741590: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 18:43:33.741615: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.embeddings)

2022-01-27T18:44:06 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T18:44:06 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-27T18:44:06 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-27T18:44:25 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.5448, train/mami/cross_entropy/avg: 0.5448, train/total_loss: 0.5448, train/total_loss/avg: 0.5448, max mem: 7107.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0., ups: 1.35, time: 37s

2022-01-27T18:46:33 | mmf.trainers.callbacks.logistics: progress: 100/2000, val/mami/cross_entropy: 0.5240, val/total_loss: 0.5240, val/mami/scoreA: 0.4357, val/mami/binary_f1: 0.0000, val/mami/roc_auc: 0.6321, num_updates: 100, epoch: 1, iterations: 100, max_updates: 2000, val_time: 45s 968ms, best_update: 100, best_iteration: 100, best_val/mami/scoreA: 0.435666
2022-01-27T18:46:51 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T18:46:51 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-27T1

2022-01-27T18:48:20 | mmf.trainers.callbacks.logistics: progress: 200/2000, train/mami/cross_entropy: 0.5448, train/mami/cross_entropy/avg: 0.5819, train/total_loss: 0.5448, train/total_loss/avg: 0.5819, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 200, iterations: 200, max_updates: 2000, lr: 0.00001, ups: 1.35, time: 37s 176ms, time_since_start: 04m 31s 896ms, eta: 23m 38s 648ms
2022-01-27T18:48:20 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T18:48:26 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, cat

2022-01-27T18:50:17 | mmf.trainers.callbacks.logistics: progress: 250/2000, val/mami/cross_entropy: 0.4732, val/total_loss: 0.4732, val/mami/scoreA: 0.5283, val/mami/binary_f1: 0.1783, val/mami/roc_auc: 0.7393, num_updates: 250, epoch: 1, iterations: 250, max_updates: 2000, val_time: 47s 029ms, best_update: 250, best_iteration: 250, best_val/mami/scoreA: 0.528298
2022-01-27T18:50:35 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T18:50:35 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-27T1

...

2022-01-27T19:26:02 | mmf.trainers.callbacks.logistics: progress: 1700/2000, train/mami/cross_entropy: 0.1770, train/mami/cross_entropy/avg: 0.3066, train/total_loss: 0.1770, train/total_loss/avg: 0.3066, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1700, iterations: 1700, max_updates: 2000, lr: 0., ups: 1.32, time: 38s 781ms, time_since_start: 42m 14s 041ms, eta: 04m 06s 649ms
2022-01-27T19:26:02 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T19:26:09 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, categ

2022-01-27T19:27:49 | mmf.trainers.callbacks.logistics: progress: 1750/2000, val/mami/cross_entropy: 0.4697, val/total_loss: 0.4697, val/mami/scoreA: 0.7425, val/mami/binary_f1: 0.5891, val/mami/roc_auc: 0.8708, num_updates: 1750, epoch: 3, iterations: 1750, max_updates: 2000, val_time: 33s 629ms, best_update: 1100, best_iteration: 1100, best_val/mami/scoreA: 0.779861
2022-01-27T19:28:07 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T19:28:07 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-27T19:29:39 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.1045, train/mami/cross_entropy/avg: 0.2867, train/total_loss: 0.1045, train/total_loss/avg: 0.2867, max mem: 7108.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 1.28, time: 39s 226ms, time_since_start: 45m 51s 772ms, eta: 02m 04s 741ms
2022-01-27T19:29:39 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T19:29:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, categ

2022-01-27T19:31:31 | mmf.trainers.callbacks.logistics: progress: 1900/2000, val/mami/cross_entropy: 0.4751, val/total_loss: 0.4751, val/mami/scoreA: 0.7403, val/mami/binary_f1: 0.5868, val/mami/roc_auc: 0.8733, num_updates: 1900, epoch: 4, iterations: 1900, max_updates: 2000, val_time: 34s 721ms, best_update: 1100, best_iteration: 1100, best_val/mami/scoreA: 0.779861
2022-01-27T19:31:49 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-27T19:31:49 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-27T19:33:18 | mmf.trainers.callbacks.logistics: progress: 2000/2000, train/mami/cross_entropy: 0.0948, train/mami/cross_entropy/avg: 0.2763, train/total_loss: 0.0948, train/total_loss/avg: 0.2763, max mem: 7108.0, experiment: run, epoch: 4, num_updates: 2000, iterations: 2000, max_updates: 2000, lr: 0., ups: 1.52, time: 33s 757ms, time_since_start: 49m 30s 031ms, eta: 0ms
2022-01-27T19:33:19 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T19:33:26 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWa

In [1]:
import os
home = "/home/taochen"
os.chdir(home)
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_objectification11.jsonl")

!mmf_run config="projects/vilbert/configs/mami/from_cc.yaml" \
        model="vilbert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2500 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_objectification.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/vilbert_objectification \
        env.tensorboard_logdir=new_logs/fit/vilbert_objectification

2022-01-27 20:44:27.978249: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-27 20:44:27.978271: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-27T20:44:30 | mmf.utils.configuration: Overriding option config to projects/vilbert/configs/mami/from_cc.yaml
2022-01-27T20:44:30 | mmf.ut

2022-01-27T20:44:40 | mmf.trainers.mmf_trainer: Loading optimizer
2022-01-27T20:44:40 | mmf.trainers.mmf_trainer: Loading metrics
()
2022-01-27T20:44:40 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-27T20:44:42 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-27T20:44:42 | mmf: Key distributed is not present in registry, returning default value of None
WARNING 2022-01-27T20:44:42 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-27T20:44:42 | mmf: Key distributed is not present in registry, returning default value of None
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.embeddings.word_embeddings.weight from model.bert.embeddings.word_embeddings.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.embeddings.position_embeddings.weight from model.bert.embeddings.position_embeddings.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying mo

2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.self.value.weight from model.bert.encoder.layer.2.attention.self.value.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.self.value.bias from model.bert.encoder.layer.2.attention.self.value.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.dense.weight from model.bert.encoder.layer.2.attention.output.dense.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.dense.bias from model.bert.encoder.layer.2.attention.output.dense.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.LayerNorm.weight from model.bert.encoder.layer.2.attention.output.LayerNorm.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.LayerNorm.bias from model.bert.encoder.layer.2.attention.

2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.5.output.LayerNorm.bias from model.bert.encoder.layer.5.output.LayerNorm.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.query.weight from model.bert.encoder.layer.6.attention.self.query.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.query.bias from model.bert.encoder.layer.6.attention.self.query.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.key.weight from model.bert.encoder.layer.6.attention.self.key.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.key.bias from model.bert.encoder.layer.6.attention.self.key.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.6.attention.self.value.weight from model.bert.encoder.layer.6.attention.self.value.weight
2022-01-27T20:44:42 | mmf.

2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.output.dense.bias from model.bert.encoder.layer.9.output.dense.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.output.LayerNorm.weight from model.bert.encoder.layer.9.output.LayerNorm.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.output.LayerNorm.bias from model.bert.encoder.layer.9.output.LayerNorm.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.query.weight from model.bert.encoder.layer.10.attention.self.query.weight
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.query.bias from model.bert.encoder.layer.10.attention.self.query.bias
2022-01-27T20:44:42 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.attention.self.key.weight from model.bert.encoder.layer.10.attention.self.key.weight
2022-01-27T20:44:42 | mmf.utils.checkpoi

...

2022-01-27T21:53:58 | mmf.trainers.callbacks.logistics: progress: 2150/2500, train/mami/cross_entropy: 0.0564, train/mami/cross_entropy/avg: 0.2657, train/total_loss: 0.0564, train/total_loss/avg: 0.2657, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 2150, iterations: 2150, max_updates: 2500, lr: 0., ups: 1.22, time: 41s 642ms, time_since_start: 01h 09m 18s 002ms, eta: 05m 08s 988ms
2022-01-27T21:53:58 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T21:54:07 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-27T21:57:03 | mmf.trainers.callbacks.logistics: progress: 2250/2500, train/mami/cross_entropy: 0.0358, train/mami/cross_entropy/avg: 0.2540, train/total_loss: 0.0358, train/total_loss/avg: 0.2540, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 2250, iterations: 2250, max_updates: 2500, lr: 0., ups: 1.02, time: 49s 768ms, time_since_start: 01h 12m 22s 532ms, eta: 04m 23s 773ms
2022-01-27T21:57:03 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T21:57:11 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-27T22:00:12 | mmf.trainers.callbacks.logistics: progress: 2350/2500, train/mami/cross_entropy: 0.0226, train/mami/cross_entropy/avg: 0.2438, train/total_loss: 0.0226, train/total_loss/avg: 0.2438, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 2350, iterations: 2350, max_updates: 2500, lr: 0., ups: 1.00, time: 50s 472ms, time_since_start: 01h 15m 31s 116ms, eta: 02m 40s 503ms
2022-01-27T22:00:12 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:00:20 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-27T22:03:09 | mmf.trainers.callbacks.logistics: progress: 2450/2500, train/mami/cross_entropy: 0.0217, train/mami/cross_entropy/avg: 0.2367, train/total_loss: 0.0217, train/total_loss/avg: 0.2367, max mem: 7253.0, experiment: run, epoch: 4, num_updates: 2450, iterations: 2450, max_updates: 2500, lr: 0., ups: 1.32, time: 38s 180ms, time_since_start: 01h 18m 28s 774ms, eta: 40s 471ms
2022-01-27T22:03:09 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-27T22:03:18 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

100%|███████████████████████████████████████████| 63/63 [00:08<00:00,  7.51it/s]
2022-01-27T22:06:04 | mmf.trainers.callbacks.logistics: progress: 1450/2500, val/mami/cross_entropy: 0.4148, val/total_loss: 0.4148, val/mami/scoreA: 0.7777, val/mami/binary_f1: 0.6564, val/mami/roc_auc: 0.8705
2022-01-27T22:06:04 | mmf.trainers.callbacks.logistics: Finished run in 01h 21m 23s 724ms


In [37]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_objectification11.jsonl")

!mmf_run config="projects/others/late_fusion/mami/defaults.yaml" \
        model="late_fusion" \
        dataset=mami \
        checkpoint.max_to_keep=1 \
        run_type=train_val \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_objectification.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/late_fusion_objectification \
        env.tensorboard_logdir=new_logs/fit/late_fusion_objectification

2022-01-28 18:11:50.258635: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 18:11:50.258659: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2022-01-28T18:11:56 | mmf.utils.configuration: Overriding option config to projects/others/late_fusion/mami/defaults.yaml
2022-01-28T18:11:56 | mmf.utils.configuration: Overriding option model to late_fusion
2022-01-28T18:11:56 | mmf.utils.configuration: Overriding option datasets to mami
2022-01-28T18:11:56 | mmf.utils.configuration: Overriding option checkpoint.max_to_keep to 1
2022-01-28T18:11:56 | mmf.utils.configuration: Overriding option run_type to train_val
2022-01-28T18:11:56 | mmf.utils.configuration: Overriding option training.tensorboard to True
2022-01-28T18:11:56 | mmf.utils.configuration: O

2022-01-28T18:12:33 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T18:12:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:12:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T18:12:39 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.7316, train/mami/cross_entropy/avg: 0.7316, train/total_loss: 0.7316, train/total_loss/avg: 0.7316, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0.00001, ups: 2.08, time

2022-01-28T18:17:59 | mmf.trainers.callbacks.logistics: progress: 200/2000, val/mami/cross_entropy: 0.5083, val/total_loss: 0.5083, val/mami/scoreA: 0.7075, val/mami/binary_f1: 0.5252, val/mami/roc_auc: 0.7688, num_updates: 200, epoch: 1, iterations: 200, max_updates: 2000, val_time: 48s 461ms, best_update: 200, best_iteration: 200, best_val/mami/scoreA: 0.707455
2022-01-28T18:18:17 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T18:18:17 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:18:17 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.

WARNING 2022-01-28T18:22:27 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:22:27 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T18:22:53 | mmf.trainers.callbacks.logistics: progress: 400/2000, val/mami/cross_entropy: 0.4612, val/total_loss: 0.4612, val/mami/scoreA: 0.7154, val/mami/binary_f1: 0.5558, val/mami/roc_auc: 0.8214, num_updates: 400, epoch: 1, iterations: 400, max_updates: 2000, val_time: 32s 622ms, best_update: 250, best_iteration: 250, best_val/mami/scoreA: 0.721750
2022-01-28T18:23:17 | mmf.trainers.callbacks.checkpoint:

2022-01-28T18:27:01 | mmf.trainers.callbacks.logistics: progress: 600/2000, train/mami/cross_entropy: 0.4804, train/mami/cross_entropy/avg: 0.4522, train/total_loss: 0.4804, train/total_loss/avg: 0.4522, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 600, iterations: 600, max_updates: 2000, lr: 0.00005, ups: 1.47, time: 34s 879ms, time_since_start: 14m 46s 571ms, eta: 17m 15s 218ms
2022-01-28T18:27:01 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:27:08 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:27:08 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when savi

...

WARNING 2022-01-28T18:40:31 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:40:31 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T18:41:14 | mmf.trainers.callbacks.logistics: progress: 1150/2000, val/mami/cross_entropy: 0.4165, val/total_loss: 0.4165, val/mami/scoreA: 0.7427, val/mami/binary_f1: 0.6151, val/mami/roc_auc: 0.8719, num_updates: 1150, epoch: 2, iterations: 1150, max_updates: 2000, val_time: 49s 227ms, best_update: 650, best_iteration: 650, best_val/mami/scoreA: 0.759768
2022-01-28T18:41:32 | mmf.trainers.callbacks.checkpoi

2022-01-28T18:45:37 | mmf.trainers.callbacks.logistics: progress: 1350/2000, train/mami/cross_entropy: 0.2664, train/mami/cross_entropy/avg: 0.3533, train/total_loss: 0.2664, train/total_loss/avg: 0.3533, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1350, iterations: 1350, max_updates: 2000, lr: 0.00002, ups: 1.22, time: 41s 159ms, time_since_start: 33m 21s 826ms, eta: 09m 27s 180ms
2022-01-28T18:45:37 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:45:43 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:45:43 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when s

2022-01-28T18:50:27 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T18:50:27 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:50:27 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T18:50:43 | mmf.trainers.callbacks.logistics: progress: 1550/2000, train/mami/cross_entropy: 0.2516, train/mami/cross_entropy/avg: 0.3307, train/total_loss: 0.2516, train/total_loss/avg: 0.3307, max mem: 7108.0, experiment: run, epoch: 3, num_updates: 1550, iterations: 1550, max_updates: 2000, lr: 0.00001, ups: 1.47

2022-01-28T18:55:03 | mmf.trainers.callbacks.logistics: progress: 1700/2000, val/mami/cross_entropy: 0.4118, val/total_loss: 0.4118, val/mami/scoreA: 0.7611, val/mami/binary_f1: 0.6338, val/mami/roc_auc: 0.8549, num_updates: 1700, epoch: 3, iterations: 1700, max_updates: 2000, val_time: 33s 205ms, best_update: 1600, best_iteration: 1600, best_val/mami/scoreA: 0.768406
2022-01-28T18:55:21 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T18:55:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:55:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warn

2022-01-28T18:59:15 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T18:59:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T18:59:21 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T18:59:48 | mmf.trainers.callbacks.logistics: progress: 1900/2000, val/mami/cross_entropy: 0.4274, val/total_loss: 0.4274, val/mami/scoreA: 0.7550, val/mami/binary_f1: 0.6299, val/mami/roc_auc: 0.8564, num_updates: 1900, epoch: 4, iterations: 1900, max_updates: 2000, val_time: 33s 147ms, best_update: 1600

## violence

In [1]:
import os
home = '/home/taochen'
os.chdir(home)
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_violence11.jsonl")

!mmf_run config="projects/others/concat_bert/mami/defaults.yaml" \
        model="concat_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=4000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_violence.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/concat_bert_violence \
        env.tensorboard_logdir=new_logs/fit/concat_bert_violence

2022-01-28 01:47:38.660981: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 01:47:38.661005: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2022-01-28T01:47:41 | mmf.utils.configuration: Overriding option config to projects/others/concat_bert/mami/defaults.yaml
2022-01-28T01:47:41 | mmf.utils.configuration: Overriding option model to concat_bert
2022-01-28T01:47:41 | mmf.utils.configuration: Overriding option datasets to mami
2022-01-28T01:47:41 | mmf.utils.configuration: Overriding option run_type to train_val
2022-01-28T01:47:41 | mmf.utils.configuration: Overriding option checkpoint.max_to_keep to 1
2022-01-28T01:47:41 | mmf.utils.configuration: Overriding option training.tensorboard to True
2022-01-28T01:47:41 | mmf.utils.configuration: O

2022-01-28T01:48:13 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T01:48:13 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T01:48:13 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T01:48:37 | mmf.trainers.callbacks.logistics: progress: 50/4000, train/mami/cross_entropy: 0.6809, train/mami/cross_entropy/avg: 0.6809, train/total_loss: 0.6809, train/total_loss/avg: 0.6809, max mem: 7100.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 4000, lr: 0., ups: 1.16, time: 43s

2022-01-28T01:52:51 | mmf.trainers.callbacks.logistics: progress: 200/4000, val/mami/cross_entropy: 0.5905, val/total_loss: 0.5905, val/mami/scoreA: 0.5070, val/mami/binary_f1: 0.1476, val/mami/roc_auc: 0.5659, num_updates: 200, epoch: 1, iterations: 200, max_updates: 4000, val_time: 31s 665ms, best_update: 150, best_iteration: 150, best_val/mami/scoreA: 0.508062
2022-01-28T01:53:09 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T01:53:09 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T01:53:09 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.

WARNING 2022-01-28T01:57:13 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T01:57:13 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T01:57:39 | mmf.trainers.callbacks.logistics: progress: 400/4000, val/mami/cross_entropy: 0.4404, val/total_loss: 0.4404, val/mami/scoreA: 0.5156, val/mami/binary_f1: 0.0870, val/mami/roc_auc: 0.6281, num_updates: 400, epoch: 1, iterations: 400, max_updates: 4000, val_time: 32s 216ms, best_update: 300, best_iteration: 300, best_val/mami/scoreA: 0.516435
2022-01-28T01:57:57 | mmf.trainers.callbacks.checkpoint:

2022-01-28T02:01:36 | mmf.trainers.callbacks.logistics: progress: 600/4000, train/mami/cross_entropy: 0.4983, train/mami/cross_entropy/avg: 0.4628, train/total_loss: 0.4983, train/total_loss/avg: 0.4628, max mem: 7100.0, experiment: run, epoch: 1, num_updates: 600, iterations: 600, max_updates: 4000, lr: 0.00002, ups: 1.39, time: 36s 089ms, time_since_start: 13m 42s 129ms, eta: 43m 21s 365ms
2022-01-28T02:01:36 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T02:01:43 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T02:01:43 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when savi

...

2022-01-28T03:07:52 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T03:07:52 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T03:07:52 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T03:08:11 | mmf.trainers.callbacks.logistics: progress: 3300/4000, train/mami/cross_entropy: 0.0367, train/mami/cross_entropy/avg: 0.2061, train/total_loss: 0.0367, train/total_loss/avg: 0.2061, max mem: 7100.0, experiment: run, epoch: 6, num_updates: 3300, iterations: 3300, max_updates: 4000, lr: 0., ups: 1.35, tim

2022-01-28T03:12:18 | mmf.trainers.callbacks.logistics: progress: 3450/4000, val/mami/cross_entropy: 0.3177, val/total_loss: 0.3177, val/mami/scoreA: 0.6993, val/mami/binary_f1: 0.4623, val/mami/roc_auc: 0.7982, num_updates: 3450, epoch: 6, iterations: 3450, max_updates: 4000, val_time: 33s 961ms, best_update: 2200, best_iteration: 2200, best_val/mami/scoreA: 0.720645
2022-01-28T03:12:37 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T03:12:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T03:12:37 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warn

WARNING 2022-01-28T03:16:51 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T03:16:51 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T03:17:20 | mmf.trainers.callbacks.logistics: progress: 3650/4000, val/mami/cross_entropy: 0.2925, val/total_loss: 0.2925, val/mami/scoreA: 0.7095, val/mami/binary_f1: 0.4731, val/mami/roc_auc: 0.7901, num_updates: 3650, epoch: 6, iterations: 3650, max_updates: 4000, val_time: 35s 017ms, best_update: 2200, best_iteration: 2200, best_val/mami/scoreA: 0.720645
2022-01-28T03:17:38 | mmf.trainers.callbacks.checkp

2022-01-28T03:21:37 | mmf.trainers.callbacks.logistics: progress: 3850/4000, train/mami/cross_entropy: 0.0274, train/mami/cross_entropy/avg: 0.1804, train/total_loss: 0.0274, train/total_loss/avg: 0.1804, max mem: 7100.0, experiment: run, epoch: 7, num_updates: 3850, iterations: 3850, max_updates: 4000, lr: 0., ups: 1.32, time: 38s 175ms, time_since_start: 01h 33m 42s 540ms, eta: 02m 01s 397ms
2022-01-28T03:21:37 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T03:21:44 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T03:21:44 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when sa

2022-01-28T03:25:41 | mmf.trainers.core.training_loop: Stepping into final validation check
2022-01-28T03:25:41 | mmf.utils.checkpoint: Restoring checkpoint
2022-01-28T03:25:41 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-28T03:25:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:218: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T03:25:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:218: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T03:25:42 | mmf.utils.checkpoint: Checkpoint loaded.
2022-01-28T03:25:42 | mmf.utils.checkpoint: Current num updates: 2200
2022-01-28T03:25:42 | mmf.utils.checkpoint: Current iteration: 2200
2

In [2]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_violence11.jsonl")

!mmf_run config="projects/mmf_transformer/configs/mami/defaults.yaml" \
        model="mmf_transformer" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=4000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_violence.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/mmf_transformer_violence \
        env.tensorboard_logdir=new_logs/fit/mmf_transformer_violence

2022-01-28 03:25:51.488765: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 03:25:51.488789: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.embeddings)

2022-01-28T03:26:23 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T03:26:23 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T03:26:23 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T03:26:30 | mmf.trainers.callbacks.logistics: progress: 50/4000, train/mami/cross_entropy: 0.4433, train/mami/cross_entropy/avg: 0.4433, train/total_loss: 0.4433, train/total_loss/avg: 0.4433, max mem: 7107.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 4000, lr: 0., ups: 2.08, time: 24s

2022-01-28T03:28:44 | mmf.trainers.callbacks.logistics: progress: 100/4000, val/mami/cross_entropy: 0.3490, val/total_loss: 0.3490, val/mami/scoreA: 0.4720, val/mami/binary_f1: 0.0000, val/mami/roc_auc: 0.5217, num_updates: 100, epoch: 1, iterations: 100, max_updates: 4000, val_time: 46s 402ms, best_update: 100, best_iteration: 100, best_val/mami/scoreA: 0.472017
2022-01-28T03:29:01 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T03:29:01 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-28T0

2022-01-28T03:30:27 | mmf.trainers.callbacks.logistics: progress: 200/4000, train/mami/cross_entropy: 0.4433, train/mami/cross_entropy/avg: 0.5258, train/total_loss: 0.4433, train/total_loss/avg: 0.5258, max mem: 7108.0, experiment: run, epoch: 1, num_updates: 200, iterations: 200, max_updates: 4000, lr: 0.00001, ups: 1.43, time: 35s 692ms, time_since_start: 04m 21s 218ms, eta: 47m 55s 376ms
2022-01-28T03:30:27 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T03:30:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, cat

2022-01-28T03:32:12 | mmf.trainers.callbacks.logistics: progress: 250/4000, val/mami/cross_entropy: 0.3278, val/total_loss: 0.3278, val/mami/scoreA: 0.4720, val/mami/binary_f1: 0.0000, val/mami/roc_auc: 0.6551, num_updates: 250, epoch: 1, iterations: 250, max_updates: 4000, val_time: 34s 746ms, best_update: 100, best_iteration: 100, best_val/mami/scoreA: 0.472017
2022-01-28T03:32:30 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T03:32:30 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01-28T0

...

2022-01-28T04:55:28 | mmf.trainers.callbacks.logistics: progress: 3700/4000, val/mami/cross_entropy: 0.5656, val/total_loss: 0.5656, val/mami/scoreA: 0.7107, val/mami/binary_f1: 0.4706, val/mami/roc_auc: 0.7954, num_updates: 3700, epoch: 7, iterations: 3700, max_updates: 4000, val_time: 36s 466ms, best_update: 1900, best_iteration: 1900, best_val/mami/scoreA: 0.738651
2022-01-28T04:55:46 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T04:55:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-28T04:57:16 | mmf.trainers.callbacks.logistics: progress: 3800/4000, train/mami/cross_entropy: 0.0018, train/mami/cross_entropy/avg: 0.1115, train/total_loss: 0.0018, train/total_loss/avg: 0.1115, max mem: 7108.0, experiment: run, epoch: 7, num_updates: 3800, iterations: 3800, max_updates: 4000, lr: 0., ups: 1.43, time: 35s 515ms, time_since_start: 01h 31m 10s 421ms, eta: 02m 30s 584ms
2022-01-28T04:57:16 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T04:57:23 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, c

2022-01-28T04:59:01 | mmf.trainers.callbacks.logistics: progress: 3850/4000, val/mami/cross_entropy: 0.5660, val/total_loss: 0.5660, val/mami/scoreA: 0.7090, val/mami/binary_f1: 0.4678, val/mami/roc_auc: 0.7964, num_updates: 3850, epoch: 7, iterations: 3850, max_updates: 4000, val_time: 34s 896ms, best_update: 1900, best_iteration: 1900, best_val/mami/scoreA: 0.738651
2022-01-28T04:59:19 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T04:59:19 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)

WARNING 2022-01

2022-01-28T05:00:44 | mmf.trainers.callbacks.logistics: progress: 3950/4000, train/mami/cross_entropy: 0.0017, train/mami/cross_entropy/avg: 0.1075, train/total_loss: 0.0017, train/total_loss/avg: 0.1075, max mem: 7108.0, experiment: run, epoch: 7, num_updates: 3950, iterations: 3950, max_updates: 4000, lr: 0., ups: 1.43, time: 35s 098ms, time_since_start: 01h 34m 38s 266ms, eta: 37s 203ms
2022-01-28T05:00:44 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T05:00:51 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (backend.transformer) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, categ

2022-01-28T05:02:28 | mmf.trainers.callbacks.logistics: progress: 4000/4000, val/mami/cross_entropy: 0.5668, val/total_loss: 0.5668, val/mami/scoreA: 0.7090, val/mami/binary_f1: 0.4678, val/mami/roc_auc: 0.7956, num_updates: 4000, epoch: 7, iterations: 4000, max_updates: 4000, val_time: 33s 393ms, best_update: 1900, best_iteration: 1900, best_val/mami/scoreA: 0.738651
2022-01-28T05:02:28 | mmf.trainers.core.training_loop: Stepping into final validation check
2022-01-28T05:02:28 | mmf.utils.checkpoint: Restoring checkpoint
2022-01-28T05:02:28 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-28T05:02:29 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:218: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T05:02:29 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_s

In [3]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_violence11.jsonl")

!mmf_run config="projects/vilbert/configs/mami/from_cc.yaml" \
        model="vilbert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=4000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_violence.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=2.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/vilbert_violence \
        env.tensorboard_logdir=new_logs/fit/vilbert_violence

2022-01-28 05:02:38.973878: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 05:02:38.973901: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T05:02:41 | mmf.utils.configuration: Overriding option config to projects/vilbert/configs/mami/from_cc.yaml
2022-01-28T05:02:41 | mmf.ut

2022-01-28T05:02:54 | mmf.trainers.mmf_trainer: Loading optimizer
2022-01-28T05:02:54 | mmf.trainers.mmf_trainer: Loading metrics
()
2022-01-28T05:02:54 | mmf.utils.checkpoint: Loading checkpoint
WARNING 2022-01-28T05:03:02 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-28T05:03:02 | mmf: Key distributed is not present in registry, returning default value of None
WARNING 2022-01-28T05:03:02 | mmf: Key data_parallel is not present in registry, returning default value of None
WARNING 2022-01-28T05:03:02 | mmf: Key distributed is not present in registry, returning default value of None
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.embeddings.word_embeddings.weight from model.bert.embeddings.word_embeddings.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.embeddings.position_embeddings.weight from model.bert.embeddings.position_embeddings.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying mo

2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.self.key.weight from model.bert.encoder.layer.3.attention.self.key.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.self.key.bias from model.bert.encoder.layer.3.attention.self.key.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.self.value.weight from model.bert.encoder.layer.3.attention.self.value.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.self.value.bias from model.bert.encoder.layer.3.attention.self.value.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.output.dense.weight from model.bert.encoder.layer.3.attention.output.dense.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.3.attention.output.dense.bias from model.bert.encoder.layer.3.attention.output.dense.bias
2022-01-28

2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.query.weight from model.bert.encoder.layer.7.attention.self.query.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.query.bias from model.bert.encoder.layer.7.attention.self.query.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.key.weight from model.bert.encoder.layer.7.attention.self.key.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.key.bias from model.bert.encoder.layer.7.attention.self.key.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.value.weight from model.bert.encoder.layer.7.attention.self.value.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.self.value.bias from model.bert.encoder.layer.7.attention.self.value.bias
2022-01-28T05:03:0

2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.10.output.LayerNorm.bias from model.bert.encoder.layer.10.output.LayerNorm.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.11.attention.self.query.weight from model.bert.encoder.layer.11.attention.self.query.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.11.attention.self.query.bias from model.bert.encoder.layer.11.attention.self.query.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.11.attention.self.key.weight from model.bert.encoder.layer.11.attention.self.key.weight
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.11.attention.self.key.bias from model.bert.encoder.layer.11.attention.self.key.bias
2022-01-28T05:03:02 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.11.attention.self.value.weight from model.bert.encoder.layer.11.attention.self.value.weight
2022-01-28T05:

...

2022-01-28T06:58:41 | mmf.trainers.callbacks.logistics: progress: 3650/4000, train/mami/cross_entropy: 0.0009, train/mami/cross_entropy/avg: 0.1289, train/total_loss: 0.0009, train/total_loss/avg: 0.1289, max mem: 7253.0, experiment: run, epoch: 6, num_updates: 3650, iterations: 3650, max_updates: 4000, lr: 0., ups: 0.94, time: 53s 235ms, time_since_start: 01h 55m 47s 135ms, eta: 06m 35s 007ms
2022-01-28T06:58:41 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T06:58:50 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-28T07:01:56 | mmf.trainers.callbacks.logistics: progress: 3750/4000, train/mami/cross_entropy: 0.0010, train/mami/cross_entropy/avg: 0.1255, train/total_loss: 0.0010, train/total_loss/avg: 0.1255, max mem: 7253.0, experiment: run, epoch: 7, num_updates: 3750, iterations: 3750, max_updates: 4000, lr: 0., ups: 0.93, time: 54s 315ms, time_since_start: 01h 59m 01s 648ms, eta: 04m 47s 871ms
2022-01-28T07:01:56 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:02:04 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-28T07:04:56 | mmf.trainers.callbacks.logistics: progress: 3850/4000, train/mami/cross_entropy: 0.0008, train/mami/cross_entropy/avg: 0.1223, train/total_loss: 0.0008, train/total_loss/avg: 0.1223, max mem: 7253.0, experiment: run, epoch: 7, num_updates: 3850, iterations: 3850, max_updates: 4000, lr: 0., ups: 1.52, time: 33s 996ms, time_since_start: 02h 02m 01s 997ms, eta: 01m 48s 107ms
2022-01-28T07:04:56 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:05:04 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-28T07:07:37 | mmf.trainers.callbacks.logistics: progress: 3950/4000, train/mami/cross_entropy: 0.0008, train/mami/cross_entropy/avg: 0.1192, train/total_loss: 0.0008, train/total_loss/avg: 0.1192, max mem: 7253.0, experiment: run, epoch: 7, num_updates: 3950, iterations: 3950, max_updates: 4000, lr: 0., ups: 1.72, time: 29s 516ms, time_since_start: 02h 04m 43s 028ms, eta: 31s 287ms
2022-01-28T07:07:37 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T07:07:46 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

100%|███████████████████████████████████████████| 63/63 [00:08<00:00,  7.45it/s]
2022-01-28T07:10:35 | mmf.trainers.callbacks.logistics: progress: 1350/4000, val/mami/cross_entropy: 0.3041, val/total_loss: 0.3041, val/mami/scoreA: 0.7402, val/mami/binary_f1: 0.5340, val/mami/roc_auc: 0.8333
2022-01-28T07:10:35 | mmf.trainers.callbacks.logistics: Finished run in 02h 07m 40s 757ms


In [38]:
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train_violence11.jsonl")

!mmf_run config="projects/visual_bert/configs/mami/from_coco.yaml" \
        model="visual_bert" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        checkpoint.resume_zoo=visual_bert.pretrained.cc.full \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=2000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val_violence.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/violence_individual \
        env.tensorboard_logdir=new_logs/fit/violence_individual

2022-01-28 19:02:32.112971: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 19:02:32.112996: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T19:02:37 | mmf.utils.configuration: Overriding option config to projects/visual_bert/configs/mami/from_coco.yaml
2022-01-28T19:02:37 | 

2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.dense.weight from model.bert.encoder.layer.2.attention.output.dense.weight
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.dense.bias from model.bert.encoder.layer.2.attention.output.dense.bias
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.LayerNorm.weight from model.bert.encoder.layer.2.attention.output.LayerNorm.weight
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.attention.output.LayerNorm.bias from model.bert.encoder.layer.2.attention.output.LayerNorm.bias
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.intermediate.dense.weight from model.bert.encoder.layer.2.intermediate.dense.weight
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.2.intermediate.dense.bias from model.bert.encoder.layer.2.intermedia

2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.dense.weight from model.bert.encoder.layer.8.output.dense.weight
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.dense.bias from model.bert.encoder.layer.8.output.dense.bias
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.LayerNorm.weight from model.bert.encoder.layer.8.output.LayerNorm.weight
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.8.output.LayerNorm.bias from model.bert.encoder.layer.8.output.LayerNorm.bias
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.attention.self.query.weight from model.bert.encoder.layer.9.attention.self.query.weight
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.9.attention.self.query.bias from model.bert.encoder.layer.9.attention.self.query.bias
2022-01-28T19:02:53 | mmf.utils.checkpoint: Copying model.

2022-01-28T19:03:12 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T19:03:12 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T19:03:12 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T19:03:16 | mmf.trainers.callbacks.logistics: progress: 50/2000, train/mami/cross_entropy: 0.3694, train/mami/cross_entropy/avg: 0.3694, train/total_loss: 0.3694, train/total_loss/avg: 0.3694, max mem: 5481.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 2000, lr: 0.00001, ups: 2.27, time

2022-01-28T19:05:35 | mmf.trainers.callbacks.logistics: progress: 150/2000, train/mami/cross_entropy: 0.3694, train/mami/cross_entropy/avg: 0.3366, train/total_loss: 0.3694, train/total_loss/avg: 0.3366, max mem: 5484.0, experiment: run, epoch: 1, num_updates: 150, iterations: 150, max_updates: 2000, lr: 0.00002, ups: 1.85, time: 27s 052ms, time_since_start: 02m 44s 776ms, eta: 17m 41s 017ms
2022-01-28T19:05:35 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T19:05:42 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=Use

...

2022-01-28T19:31:26 | mmf.trainers.callbacks.logistics: progress: 1650/2000, train/mami/cross_entropy: 0.0940, train/mami/cross_entropy/avg: 0.2125, train/total_loss: 0.0940, train/total_loss/avg: 0.2125, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1650, iterations: 1650, max_updates: 2000, lr: 0.00001, ups: 2.00, time: 25s 423ms, time_since_start: 28m 36s 064ms, eta: 03m 08s 641ms
2022-01-28T19:31:26 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T19:31:33 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=

2022-01-28T19:33:04 | mmf.trainers.callbacks.logistics: progress: 1750/2000, train/mami/cross_entropy: 0.0938, train/mami/cross_entropy/avg: 0.2073, train/total_loss: 0.0938, train/total_loss/avg: 0.2073, max mem: 5484.0, experiment: run, epoch: 3, num_updates: 1750, iterations: 1750, max_updates: 2000, lr: 0., ups: 2.00, time: 25s 471ms, time_since_start: 30m 13s 870ms, eta: 02m 14s 996ms
2022-01-28T19:33:04 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T19:33:11 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T19:34:49 | mmf.trainers.callbacks.logistics: progress: 1850/2000, train/mami/cross_entropy: 0.0665, train/mami/cross_entropy/avg: 0.1995, train/total_loss: 0.0665, train/total_loss/avg: 0.1995, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1850, iterations: 1850, max_updates: 2000, lr: 0., ups: 2.00, time: 25s 838ms, time_since_start: 31m 59s 110ms, eta: 01m 22s 167ms
2022-01-28T19:34:49 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T19:34:56 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

2022-01-28T19:36:28 | mmf.trainers.callbacks.logistics: progress: 1950/2000, train/mami/cross_entropy: 0.0599, train/mami/cross_entropy/avg: 0.1899, train/total_loss: 0.0599, train/total_loss/avg: 0.1899, max mem: 5484.0, experiment: run, epoch: 4, num_updates: 1950, iterations: 1950, max_updates: 2000, lr: 0., ups: 2.00, time: 25s 702ms, time_since_start: 33m 38s 348ms, eta: 27s 245ms
2022-01-28T19:36:28 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T19:36:36 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarni

100%|███████████████████████████████████████████| 63/63 [00:07<00:00,  8.79it/s]
2022-01-28T19:38:02 | mmf.trainers.callbacks.logistics: progress: 1100/2000, val/mami/cross_entropy: 0.2742, val/total_loss: 0.2742, val/mami/scoreA: 0.7179, val/mami/binary_f1: 0.4815, val/mami/roc_auc: 0.7914
2022-01-28T19:38:02 | mmf.trainers.callbacks.logistics: Finished run in 35m 12s 241ms


## Multi-task learning

In [6]:
import os
home = "/home/taochen"
os.chdir(home)
feats_dir = os.path.join(home, "new_features")
train_dir = os.path.join(home, "mmf/data/datasets/mami/defaults/annotations/train11.jsonl")

!mmf_run config="projects/multi_task/configs/mami/from_coco.yaml" \
        model="multi_task" \
        dataset=mami \
        run_type=train_val \
        checkpoint.max_to_keep=1 \
        checkpoint.resume_zoo=visual_bert.pretrained.cc.full \
        training.tensorboard=True \
        training.checkpoint_interval=50 \
        training.evaluation_interval=50 \
        training.max_updates=3000 \
        training.log_interval=50 \
        dataset_config.mami.max_features=100 \
        dataset_config.mami.annotations.train[0]=$train_dir \
        dataset_config.mami.annotations.val[0]=mami/defaults/annotations/val1.jsonl \
        dataset_config.mami.features.train[0]=$feats_dir \
        dataset_config.mami.features.val[0]=$feats_dir \
        training.lr_ratio=0.6 \
        training.use_warmup=True \
        training.batch_size=16 \
        optimizer.params.lr=5.0e-05 \
        scheduler.type=warmup_cosine \
        scheduler.params.num_warmup_steps=500 \
        env.save_dir=new_model_testing/multi_task_bce_kl_combined \
        env.tensorboard_logdir=new_logs/fit/multi_task_bce_kl_combined

2022-01-28 12:52:49.963685: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 12:52:49.963708: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T12:52:52 | mmf.utils.configuration: Overriding option config to projects/multi_task/configs/mami/from_coco.yaml
2022-01-28T12:52:52 | m

2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.dense.weight from model.bert.encoder.layer.1.attention.output.dense.weight
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.dense.bias from model.bert.encoder.layer.1.attention.output.dense.bias
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.LayerNorm.weight from model.bert.encoder.layer.1.attention.output.LayerNorm.weight
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.attention.output.LayerNorm.bias from model.bert.encoder.layer.1.attention.output.LayerNorm.bias
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.intermediate.dense.weight from model.bert.encoder.layer.1.intermediate.dense.weight
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.1.intermediate.dense.bias from model.bert.encoder.layer.1.intermedia

2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.attention.output.LayerNorm.bias from model.bert.encoder.layer.7.attention.output.LayerNorm.bias
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.intermediate.dense.weight from model.bert.encoder.layer.7.intermediate.dense.weight
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.intermediate.dense.bias from model.bert.encoder.layer.7.intermediate.dense.bias
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.output.dense.weight from model.bert.encoder.layer.7.output.dense.weight
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.output.dense.bias from model.bert.encoder.layer.7.output.dense.bias
2022-01-28T12:53:03 | mmf.utils.checkpoint: Copying model.bert.encoder.layer.7.output.LayerNorm.weight from model.bert.encoder.layer.7.output.LayerNorm.weight
2022-01-28T12:53:03 | mmf.utils.checkpoint: Co

2022-01-28T12:53:18 | mmf.trainers.callbacks.checkpoint: Checkpoint time. Saving a checkpoint.
WARNING 2022-01-28T12:53:18 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

WARNING 2022-01-28T12:53:18 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/torch/optim/lr_scheduler.py:200: UserWarning: Please also save or load the state of the optimzer when saving or loading the scheduler.
  warnings.warn(SAVE_STATE_WARNING, UserWarning)

2022-01-28T12:53:34 | mmf.trainers.callbacks.logistics: progress: 50/3000, train/mami/bce_kl_combined: 3.1817, train/mami/bce_kl_combined/avg: 3.1817, train/total_loss: 3.1817, train/total_loss/avg: 3.1817, max mem: 5522.0, experiment: run, epoch: 1, num_updates: 50, iterations: 50, max_updates: 3000, lr: 0.00001, ups: 1.67, 

2022-01-28T12:55:12 | mmf.trainers.callbacks.logistics: progress: 150/3000, train/mami/bce_kl_combined: 2.7007, train/mami/bce_kl_combined/avg: 2.6823, train/total_loss: 2.7007, train/total_loss/avg: 2.6823, max mem: 5524.0, experiment: run, epoch: 1, num_updates: 150, iterations: 150, max_updates: 3000, lr: 0.00002, ups: 2.94, time: 17s 839ms, time_since_start: 02m 09s 463ms, eta: 17m 57s 887ms
2022-01-28T12:55:12 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T12:55:25 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category

...

2022-01-28T13:39:53 | mmf.trainers.callbacks.logistics: progress: 2650/3000, train/mami/bce_kl_combined: 0.8460, train/mami/bce_kl_combined/avg: 1.5957, train/total_loss: 0.8460, train/total_loss/avg: 1.5957, max mem: 5524.0, experiment: run, epoch: 5, num_updates: 2650, iterations: 2650, max_updates: 3000, lr: 0., ups: 2.94, time: 17s 858ms, time_since_start: 46m 50s 442ms, eta: 02m 12s 508ms
2022-01-28T13:39:53 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T13:40:06 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-28T13:41:38 | mmf.trainers.callbacks.logistics: progress: 2750/3000, train/mami/bce_kl_combined: 0.7938, train/mami/bce_kl_combined/avg: 1.5638, train/total_loss: 0.7938, train/total_loss/avg: 1.5638, max mem: 5524.0, experiment: run, epoch: 5, num_updates: 2750, iterations: 2750, max_updates: 3000, lr: 0., ups: 2.00, time: 25s 534ms, time_since_start: 48m 35s 839ms, eta: 02m 15s 334ms
2022-01-28T13:41:38 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T13:41:45 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-28T13:43:20 | mmf.trainers.callbacks.logistics: progress: 2850/3000, train/mami/bce_kl_combined: 0.7905, train/mami/bce_kl_combined/avg: 1.5253, train/total_loss: 0.7905, train/total_loss/avg: 1.5253, max mem: 5524.0, experiment: run, epoch: 5, num_updates: 2850, iterations: 2850, max_updates: 3000, lr: 0., ups: 2.00, time: 25s 563ms, time_since_start: 50m 18s 212ms, eta: 01m 21s 290ms
2022-01-28T13:43:20 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T13:43:28 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=U

2022-01-28T13:45:01 | mmf.trainers.callbacks.logistics: progress: 2950/3000, train/mami/bce_kl_combined: 0.7733, train/mami/bce_kl_combined/avg: 1.4878, train/total_loss: 0.7733, train/total_loss/avg: 1.4878, max mem: 5524.0, experiment: run, epoch: 5, num_updates: 2950, iterations: 2950, max_updates: 3000, lr: 0., ups: 2.08, time: 24s 908ms, time_since_start: 51m 58s 797ms, eta: 26s 403ms
2022-01-28T13:45:01 | mmf.trainers.core.training_loop: Evaluation time. Running on full validation set...
WARNING 2022-01-28T13:45:08 | py.warnings: /home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserW

100%|███████████████████████████████████████████| 63/63 [00:07<00:00,  8.63it/s]
2022-01-28T13:46:36 | mmf.trainers.callbacks.logistics: progress: 2150/3000, val/mami/bce_kl_combined: 2.4667, val/total_loss: 2.4667, val/mami/scoreA: 0.8382, val/mami/scoreB: 0.7410, val/mami/roc_auc: 0.6234
2022-01-28T13:46:36 | mmf.trainers.callbacks.logistics: Finished run in 53m 33s 481ms


In [41]:
import os
home = "/home/taochen"
os.chdir(home)
# where checkpoint is
ckpt_dir = os.path.join(home, "new_model_testing/multi_task_bce_kl_combined/best.ckpt")
# Define where image features are
feats_dir = os.path.join(home, "new_features")

!mmf_predict config="projects/multi_task/configs/mami/defaults.yaml" \
    model="multi_task" \
    dataset=mami \
    run_type=test \
    checkpoint.resume_file=$ckpt_dir \
    checkpoint.reset.optimizer=True \
    dataset_config.mami.annotations.test[0]=mami/defaults/annotations/val1.jsonl \
    dataset_config.mami.features.test[0]=$feats_dir \
    env.report_dir=save/new_mami

2022-01-30 11:20:11.906333: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-30 11:20:11.906358: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-30T11:20:14 | mmf.utils.configuration: Overriding option config to projects/multi_task/configs/mami/defaults.yaml
2022-01-30T11:20:14 | mm

In [10]:
import os
home = "/home/taochen"
os.chdir(home)
# where checkpoint is
ckpt_dir = os.path.join(home, "new_model_testing/multi_task_bce_kl_combined/best.ckpt")
# Define where image features are
feats_dir = os.path.join(home, "test_features")

!mmf_predict config="projects/multi_task/configs/mami/defaults.yaml" \
    model="multi_task" \
    dataset=mami \
    run_type=test \
    checkpoint.resume_file=$ckpt_dir \
    checkpoint.reset.optimizer=True \
    dataset_config.mami.annotations.test[0]=mami/defaults/annotations/test.jsonl \
    dataset_config.mami.features.test[0]=$feats_dir \
    env.report_dir=save/new_mami_submission

2022-01-28 13:55:20.965344: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2022-01-28 13:55:20.965369: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/yewlee/miniconda3/envs/mmf/lib/python3.7/site-packages/omegaconf/dictconfig.py:252: UserWarning: Keys with dot (model.bert) are deprecated and will have different semantic meaning the next major version of OmegaConf (2.1)
See the compact keys issue for more details: https://github.com/omry/omegaconf/issues/152
You can disable this warning by setting the environment variable OC_DISABLE_DOT_ACCESS_WARNING=1
  warnings.warn(message=msg, category=UserWarning)
2022-01-28T13:55:23 | mmf.utils.configuration: Overriding option config to projects/multi_task/configs/mami/defaults.yaml
2022-01-28T13:55:23 | mm

In [16]:
import pandas as pd
path = 'save/new_mami_submission/multi_task.csv'
multi_task = pd.read_csv(path, sep=',')
multi_task

id  misogynous  shaming  stereotype  objectification  violence
0    15236.jpg           1        0           0                0         0
1    15805.jpg           1        1           1                0         0
2    16254.jpg           1        0           0                0         0
3    16191.jpg           1        0           0                1         0
4    15952.jpg           0        0           0                0         0
..         ...         ...      ...         ...              ...       ...
995  15591.jpg           1        0           1                1         0
996  15049.jpg           1        1           1                0         0
997  15363.jpg           1        0           0                1         0
998  15199.jpg           1        0           0                1         0
999  15853.jpg           1        0           0                0         0

[1000 rows x 6 columns]

In [17]:
# temp = multi_task[multi_task.iloc[:,1] == 0]
# temp = temp.iloc[:,2:].sum(axis=1) > 1
# temp = temp.loc[temp == True].index.to_list()
# multi_task.iloc[temp,1] = 1

# filter_ = multi_task.iloc[:,1] == 0
# multi_task[filter_] = multi_task[filter_].replace(1, 0)

out_path = 'answer_mul.txt'
multi_task.to_csv(out_path, header=False, index=False, sep='\t')